# Amazon Best Sellers

# Import Libraries

In [1]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
import seaborn as sns 
# this statement allows the visuals to render within your Jupyter Notebook
%matplotlib inline 
# You can configure the format of the images: ‘png’, ‘retina’, ‘jpeg’, ‘svg’, ‘pdf’.
%config InlineBackend.figure_format = 'png'
import csv

In [2]:
# Project for best sales in amazon.sa

# Best Sellers in Electronics (Page 1)

In [3]:
header = {'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/96.0.4664.45 Safari/537.36'}
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/?ie=UTF8&ref_=sv_sv_elec_all_1"

In [4]:
response = requests.get(url, {'headers':header})
response.status_code

200

In [5]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

# BeautifulSoup Basics

In [6]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [7]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [8]:
soup.find_all('li', {'class':'zg-item-immersion'})[0].find_all('a')[1].text

'\n3.0 out of 5 stars\n'

In [9]:
# create function to clean data 

In [10]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [11]:
#Test with the first electroni product to ensure functions are working
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))


SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)
3.0 out of 5 stars
3.0
2
2
SAR 539.00
539.00


In [12]:
soup.find_all("li", class_ = "zg-item-immersion")[3] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#4</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/SAMSUNG-Galaxy-M12-Dual-Smartphone/dp/B08XY5X3J7?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)" height="200" src="https://images-na.ssl-images-amazon.com/images/I/81DCMeVrbKS._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)
   

In [13]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

    

In [14]:
products_list

[{'pro_name': 'SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)',
  'pro_rate': '3.0 out of 5 stars',
  'pro_rate_clean': '3.0',
  'review_num': '2',
  'review_num_clean': '2',
  'pro_price': 'SAR 539.00',
  'pro_price_clean': '539.00'},
 {'pro_name': 'Samsung Galaxy A12 LTE Dual SIM Smartphone - 64GB Storage, 4GB RAM, Blue (KSA Version)',
  'pro_rate': '1.0 out of 5 stars',
  'pro_rate_clean': '1.0',
  'review_num': '2',
  'review_num_clean': '2',
  'pro_price': 'SAR 539.00',
  'pro_price_clean': '539.00'},
 {'pro_name': 'Apple 20W USB-C Power Adapter, White',
  'pro_rate': '4.5 out of 5 stars',
  'pro_rate_clean': '4.5',
  'review_num': '359',
  'review_num_clean': '359',
  'pro_price': 'SAR 79.00',
  'pro_price_clean': '79.00'},
 {'pro_name': 'SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)',
  'pro_rate': '4.1 out of 5 stars',
  'pro_rate_clean': '4.1',
  'review_num': '40',
  'review_num_clean': '40',
  'pro_price

In [30]:
products_df1 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df1

pro_name            pro_rate  \
0     ViewSonic M1 Mini DLP Pico Projector, 50 Lumens  4.0 out of 5 stars   
1                         BenQ Portable Projector GV1  3.5 out of 5 stars   
2   MO C9 Mini LED Projector Supports Full HD 1080...  3.2 out of 5 stars   
3   Mini Projector, ELIKLIV Native 1080P Projector...  1.7 out of 5 stars   
4   MOTIM YG300 LED Projector 1080P Projection Mac...                 NaN   
5   Epson EB-FH06 3LCD, Full HD, 3500 Lumens, 332 ...  4.4 out of 5 stars   
6   Aproca Hard Travel Case Compatible with Anker ...  4.9 out of 5 stars   
7   Annefish Projector Portable Wifi Wireless High...                 NaN   
8   DLP Link 3D Gl 144Hz Rechargeable 3D Active Sh...  4.3 out of 5 stars   
9               Mini Smart Android Wireless Projector  2.7 out of 5 stars   
10  Epson EF-11 3LCD, Full HD, Laser, 1,000 Lumens...  4.4 out of 5 stars   
11  KODAK Luma 150 Ultra Mini Pocket Pico Projecto...  4.2 out of 5 stars   
12  Epson EH-TW7400 3LCD, 4K Pro UHD Super Resolut...  4.8 out of 5 stars   
13  J&H Professional Full HD 1080P [Bluetooth] Sup...                 NaN   
14  Hd 1080p Multimedia Led Mini Projector Home Ci...  1.4 out of 5 stars   
15  BYINTEK U50 PRO 700 Ansi Lumens 300"Inch Nativ...  5.0 out of 5 stars   
16    Full HD Smart Android Projector, White - 546332  3.4 out of 5 stars   
17  Video Projector Android Smart LED Projector R1...  3.9 out of 5 stars   
18  NEBULA D2323211 by Anker Mars II Pro 500 ANSI ...  3.3 out of 5 stars   
19  Galaxy Star Night Light for Kids - Fanrui Sola...                 NaN   
20  Projector, TOPTRO Projector with WiFi and Blue...  4.2 out of 5 stars   
21  Fegishilly 3 in 1 Star Galaxy Projector Moving...  5.0 out of 5 stars   
22  ViewSonic M1+ DLP Smart Pico Projector, 300 Lu...  4.0 out of 5 stars   
23  Starry Night Light Projector for Bedroom，Sky G...  4.5 out of 5 stars   
24                   Compatible For Samsung projector  3.0 out of 5 stars   
25  Epson EB-E10 3LCD, 3600 Lumens Brightness, 15,...  3.0 out of 5 stars   
26  BenQ Full HD 3D Projector , DLP , White , MS52...  4.4 out of 5 stars   
27  Home Projector, bonsaii 5500L WiFi Projector f...  3.6 out of 5 stars   
28                   Compatible For Samsung projector  3.4 out of 5 stars   
29  Mini Projector 2600 Lumens 2019 Upgraded Porta...                 NaN   
30  Portable Mini LED Projector Home Cinema Theate...  3.2 out of 5 stars   
31  Anker Nebula Apollo, Wi-Fi Mini Projector, 200...  4.1 out of 5 stars   
32  Lixinju Laser Star Projector,star light projec...  4.5 out of 5 stars   
33  Becailyer Galaxy Star Projector Night Light wi...                 NaN   
34  ViewSonic M1+_G2 Portable Smart Wi-Fi LED Port...                 NaN   
35                             LED Projector - YG-510  2.3 out of 5 stars   
36  NXENTC Star Projector, Star Projector Light wi...  4.4 out of 5 stars   
37  Viewsonic M1 Mini Plus Pocket Led Ultra Portab...  3.8 out of 5 stars   
38  ViewSonic PA503X XGA Business Projector, 3.600...  4.4 out of 5 stars   
39    Optoma LG LED Projector with HD Imaging, PH150G  3.3 out of 5 stars   
40  Epson EH-LS500W ATV 3LCD, 4K PRO-UHD, Laser, U...  4.2 out of 5 stars   
41  BenQ TH685i 1080p Gaming Projector - 4K HDR Su...  5.0 out of 5 stars   
42  BenQ EX600 XGA Smart Portable Projector, DLP, ...  3.6 out of 5 stars   
43  1080P HD Projector, WiFi Projector Bluetooth P...  4.2 out of 5 stars   
44                   Compatible For Samsung projector  5.0 out of 5 stars   
45  ViewSonic Ultra-Portable LED Projector WVGA 25...                 NaN   
46  KADISTAR D05E mini media projector wallpaper p...                 NaN   
47  PHLIGHT Mini Projector, Home projector 800 Lum...                 NaN   
48  Mini YG300 LCD Projector 400 - 600 Lumens 320 ...  3.6 out of 5 stars   
49  KODAK Luma 350 Portable Smart Projector w/Luma...  4.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean      pro_price pro_price_clean  
0             4.0      3,030          

# Best Sellers in   Electronics (Page 2)

In [31]:
url = 'https://www.amazon.sa/-/en/gp/bestsellers/electronics/ref=zg_bs_pg_2?ie=UTF8&pg=2'

In [32]:
response = requests.get(url)
response.status_code

200

In [33]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [34]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [35]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [36]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.2 out of 5 stars\n'

In [37]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [38]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal Gaming SSD M.2 (MZ-V8P500B)
4.8 out of 5 stars
4.8
2,581
2581
SAR 311.63
311.63


In [39]:
soup.find_all("li", class_ = "zg-item-immersion")[1] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#52</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/SAMSUNG-Galaxy-Tab-Lite-Tablet/dp/B095WBLGXX?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB RAM, LTE, Gray (KSA Version)" height="200" src="https://images-na.ssl-images-amazon.com/images/I/41ZKC4i2pGS._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB RAM, LTE, Gray (KSA Version)
        </div>
</a>
<div

In [40]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [41]:
products_df2 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df2

pro_name            pro_rate  \
0   SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal ...  4.8 out of 5 stars   
1   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
2   Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
3   2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
4   Xiaomi Mi Box S - 4K Ultra HDR Android TV Stre...  4.2 out of 5 stars   
5   Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
6      Apple iPhone 12 With FaceTime (256GB) - Purple  4.4 out of 5 stars   
7   Samsung Galaxy S20 FE 4G Android Smartphone, 1...                 NaN   
8   6 PCS Camera Cover,Sliding Webcam Cover,Ultra ...  4.4 out of 5 stars   
9   MSI MPG Z490 Gaming Plus Gaming Motherboard (A...  4.6 out of 5 stars   
10  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
11  YISK Store Extended Large Gaming Mouse Pad XL ...  4.2 out of 5 stars   
12  SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.1 out of 5 stars   
13  UGREEN 65W USB C Charger Plug 4 Port GaN Type ...  4.2 out of 5 stars   
14  Bluetooth Wireless Headphones 40 Hours Playtim...  4.3 out of 5 stars   
15  Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
16  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
17  ZORD PHANTOM-1 GAMING PC, RYZEN 3 3200G, 16GB ...  3.3 out of 5 stars   
18  Samsung Galaxy SM-R175 Wireless Buds Plus with...  4.2 out of 5 stars   
19  UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
20  Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.3 out of 5 stars   
21  Samsung Galaxy S20 FE Dual SIM - 128GB, 8GB RA...  4.1 out of 5 stars   
22  Thermal Grizzly Kryonaut 12.5 W / m · K 1 g th...  4.7 out of 5 stars   
23       Apple iPhone 12 With FaceTime (128GB) - Blue  4.4 out of 5 stars   
24  Amazon Kindle Paperwhite Water-Safe Fabric Cov...  4.7 out of 5 stars   
25  Seagate BarraCuda 4TB Internal Hard Drive HDD ...  4.7 out of 5 stars   
26  UGREEN 2 Pack Screen Protector for iPhone 13/1...  4.4 out of 5 stars   
27  HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
28  FLIZIL Fast Charging Universal Travel Adapter,...  4.5 out of 5 stars   
29  HP 652 Ink Advantage Cartridge, Tri-color - F6...  4.4 out of 5 stars   
30  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
31  SAMSUNG 970 EVO Plus SSD 2TB - M.2 NVMe Interf...  4.9 out of 5 stars   
32  SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
33  Large Gaming Mousepad World Map Game Mouse Pad...  4.2 out of 5 stars   
34  UGREEN Clear iPhone 12/12Pro Case Compatible F...  4.1 out of 5 stars   
35  Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
36  Anker USB C Charger, 20W PIQ 3.0 Fast Charger ...  4.2 out of 5 stars   
37  UGREEN iPhone Charger PD20W USB C iPhone 13 Fa...  4.2 out of 5 stars   
38  Power Bank Portable Charger 10000mAh with cabl...  4.0 out of 5 stars   
39  TP-Link AC1200 Whole-Home Mesh Wi-Fi System(DE...  4.2 out of 5 stars   
40  Apple Watch Series 6 (GPS, 40mm) - Space Grey ...  4.6 out of 5 stars   
41  Desk, Laptop Desk Bed Foldable Lazy Small Tabl...  3.9 out of 5 stars   
42  UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
43  Anker Alkaline AAA Batteries (4-Pack), Long-La...  4.5 out of 5 stars   
44                                   New Apple AirTag  4.7 out of 5 stars   
45  Apple MagSafe Charger Qi/PMA for iPhone 13 Pro...  4.1 out of 5 stars   
46  2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
47  Logitech C922 Pro Stream Webcam, HD 1080p/30fp...  4.6 out of 5 stars   
48  Fasgear USB C Cable for Oculus Quest Link 2, 9...  4.0 out of 5 stars   
49  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.8      2,581           

# Best Sellers in Camera & Photo Products (Page 1)

In [42]:
url = 'https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966385031/ref=zg_bs_nav_1_electronics'

In [43]:
response = requests.get(url)
response.status_code

200

In [44]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [45]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [46]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [47]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [48]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [49]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiFi Smart Home Security Camera IR Night Vision Motion Detection Auto Tracking Baby/Elder/Pet Cloud Storage/SD Slot 2-Way Audio Wi-Fi 2.4G iOS Android App
4.2 out of 5 stars
4.2
1,410
1410
SAR 98.00
98.00


In [35]:
soup.find_all("li", class_ = "zg-item-immersion")[1] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#2</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/EZVIZ-Indoor-Security-Camera-Android/dp/B07ZC1Q6W6?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="EZVIZ C6N FHD Indoor Security Camera WiFi Smart 2.4G with iOS and Android App" height="200" src="https://images-na.ssl-images-amazon.com/images/I/51bA8A2cU9L._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            EZVIZ C6N FHD Indoor Security Camera WiFi Smart 2.4G with iOS and Android App
        </div

In [51]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [52]:
products_df3 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df3

pro_name            pro_rate  \
0   EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiF...  4.2 out of 5 stars   
1   EZVIZ C6N FHD Indoor Security Camera WiFi Smar...  4.3 out of 5 stars   
2   6 PCS Camera Cover,Sliding Webcam Cover,Ultra ...  4.4 out of 5 stars   
3   SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
4   SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
5     Kioxia Exceria 64GB MicroSD Card - LMEX1L064GG2  4.6 out of 5 stars   
6   AmazonBasics Braided 4K HDMI to HDMI Cable - 3...  4.7 out of 5 stars   
7   Eufy Indoor Cam 2K Pan & Tilt Home Security Ca...  4.5 out of 5 stars   
8   EZVIZ C2C 1080P Smart Home Security Wifi Camer...                 NaN   
9   Imou 360 Degree WiFi Security Camera, Up to 25...  3.4 out of 5 stars   
10  Panasonic Eneloop Pro Individual Cell Battery ...  4.0 out of 5 stars   
11  DJI Osmo Mobile 3 Combo - 3-Axis Gimbal Stabil...  4.6 out of 5 stars   
12  AmazonBasics High-Speed 4K HDMI Cable, 3 Feet,...  4.6 out of 5 stars   
13  Selfie Stick Tripod,Eocean 40 inch Extendable ...  4.0 out of 5 stars   
14  EZVIZ C6TC, 1080p WiFi Smart Home Security Cam...  4.4 out of 5 stars   
15        SanDisk Extreme microSDXC UHS-I Card- 128GB  4.4 out of 5 stars   
16  eufy Security, eufyCam 2 Pro Wireless Home Sec...  4.5 out of 5 stars   
17  UGREEN 8K HDMI Cable Ultra HD High Speed 48Gbp...  4.5 out of 5 stars   
18  SanDisk 256GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
19  SanDisk 128GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
20  Imou 4MP Full HD, IP 67 Outdoor Bullet Securit...  3.0 out of 5 stars   
21  Imou 4MP IP 67 Outdoor Security Camera, Color ...                 NaN   
22  Imou 360 Degree Security Camera,Up to 256GB SD...  4.3 out of 5 stars   
23  Microphone Stand Set Heavy Duty Mic Suspension...  3.5 out of 5 stars   
24  AccLoo Kids Camera 1080P HD Digital Video Toy ...  3.8 out of 5 stars   
25  Professional Camera Tripod Mount Stand Holder ...  2.1 out of 5 stars   
26  UGREEN 8K HDMI 2.1 Cable Ultra High-Speed 48Gb...  4.6 out of 5 stars   
27                 Rode Dynamic Podcasting Microphone  4.8 out of 5 stars   
28  Selfie Stick Tripod, Eocean 54 inch Extendable...  4.3 out of 5 stars   
29  Sandisk 128 GB Memory Card For Multi - Micro S...  4.2 out of 5 stars   
30  Neewer 50-In-1 Action Camera Accessory Kit, Co...  4.4 out of 5 stars   
31        Xiaomi Mi Home Security Camera 360° - White  4.0 out of 5 stars   
32  NATNO 3-in-1 USB Battery Charger Replacement f...                 NaN   
33  SanDisk Ultra microSDXC 64GB 100MB/s Class 10 ...  4.4 out of 5 stars   
34  eufy Security 2K Indoor Cam, Home Security Ind...  4.5 out of 5 stars   
35  BOYA BY M1 Lavalier Microphone for Smartphones...  3.9 out of 5 stars   
36  AmazonBasics CL2 Rated HDMI Input to VGA DVI O...  4.6 out of 5 stars   
37  UGREEN 8K HDMI Cable Ultra HD High Speed 48Gbp...  4.5 out of 5 stars   
38  UGREEN Micro HDMI to HDMI Adapter Cable Male t...  4.6 out of 5 stars   
39  YSK-Replacement Remote control for Class pro s...  5.0 out of 5 stars   
40  GTHUNDER Digital Night Vision Goggles Binocula...  4.3 out of 5 stars   
41  SanDisk 32GB Ultra microSDHC UHS-I Memory Card...  4.7 out of 5 stars   
42   KIOXIA Exceria 32GB Micro SD Card - LMEX1L032GG2  4.6 out of 5 stars   
43  SanDisk 32GB Ultra® microSDHC 120MB/s A1 Class...  4.4 out of 5 stars   
44        SanDisk Extreme microSDXC UHS-I Card- 256GB  4.4 out of 5 stars   
45        SanDisk Extreme microSDXC UHS-I Card- 512GB  4.4 out of 5 stars   
46  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
47  SanDisk 64GB microSDXC-Card-Licensed for Ninte...  4.8 out of 5 stars   
48       SanDisk Ultra 128GB SDXC Memory Card 120MB/s  4.7 out of 5 stars   
49     Sony Cyber-Shot DSC-W800-20.1 MegaPixel, Black  4.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.2      1,410             

# Best Sellers in Camera & Photo Products (Page 2)

In [53]:
url ='https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966385031/ref=zg_bs_pg_2?ie=UTF8&pg=2'

In [54]:
response = requests.get(url)
response.status_code

200

In [55]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [56]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [57]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [58]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.2 out of 5 stars\n'

In [59]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [60]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN 8K DisplayPort Cable Ultra HD DisplayPort 1.4 Male to Male Nylon Braided Cable SPCC Shell, Support 7680x4320 Resolution 8K@60Hz, 4K@144Hz, 2K@165Hz HDP HDCP Compatible for Gaming Monitor-3Meter
4.6 out of 5 stars
4.6
315
315
SAR 92.00
92.00


In [61]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [62]:
products_df4 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df4

pro_name            pro_rate  \
0   UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
1   (Single Pack) - Carson MicroBrite Plus 60 -120...  4.2 out of 5 stars   
2   EZVIZ Wifi Smart Security Camera 360 Degree, D...  4.2 out of 5 stars   
3   1.6 x 3M / 5 x 10FT Photography Studio Non-wov...  4.1 out of 5 stars   
4   EZVIZ C1C-B WiFi Security Camera, 12 Meters Ni...  4.1 out of 5 stars   
5   Phone Tripod,136cm Extendable Tripod Stand wit...  4.3 out of 5 stars   
6   Rankie Mini HDMI to HDMI Cable, High Speed Sup...  4.6 out of 5 stars   
7   eufy Security, eufyCam 2 Pro Wireless Home Sec...  4.5 out of 5 stars   
8   Xiaomi Mi Home Security Camera 360 Degrees 2K ...  4.2 out of 5 stars   
9   CanaKit Raspberry Pi 4 8GB Extreme Kit - 128GB...  4.8 out of 5 stars   
10  UGREEN 4K UHD DP to HDMI Cable Male to Male Di...  4.5 out of 5 stars   
11       Canon EOS Digital Camera, Black - 250D 18-55  4.5 out of 5 stars   
12  FitStill 3 Way Tripod for GoPro Hero 10/9/8/7/...  4.3 out of 5 stars   
13  Television Table Top Base stand Steel, Black, ...  4.1 out of 5 stars   
14  AccLoo Mini WiFi Camera, HD 1080P Wireless Por...  3.4 out of 5 stars   
15        Canon EF 50mm f/1.8 STM Standard Lens,Black  4.8 out of 5 stars   
16  eufy Security 2K Indoor Cam Pan & Tilt, Home S...  4.6 out of 5 stars   
17                    SMARTLINK HDMI 4K UHD CABLE 10m  5.0 out of 5 stars   
18  DJI Pocket 2 - 3 Axis Handheld Gimbal Stabiliz...  4.2 out of 5 stars   
19  FiTSTILL Waterproof Protective Underwater 60M ...  4.6 out of 5 stars   
20  UGREEN HDMI Cable Extension Male to Female HDM...  4.7 out of 5 stars   
21  Mini Camera,Phomnd Mini Camera Cordless WiFi R...  3.4 out of 5 stars   
22  SanDisk 256GB microSDXC Card, Licensed for Nin...  4.9 out of 5 stars   
23  FK Kids Camera for Girls and Boys, Kids Digita...                 NaN   
24  EZVIZ CS-CV310-A0-1C2WFR C3WN 1080p Outdoor Wi...  3.3 out of 5 stars   
25  SanDisk 512GB Extreme microSDXC UHS-I Memory C...  4.8 out of 5 stars   
26  UGREEN 8K HDMI 2.1 Cable Ultra High-Speed 48Gb...  4.6 out of 5 stars   
27  YG-300 LCD Mini Portable Projector with USB/SD...  2.6 out of 5 stars   
28                         Apple Pencil Tips - 4 pack  4.8 out of 5 stars   
29  MASiKEN Hard Case for Nebula Apollo Wi-Fi Mini...  4.4 out of 5 stars   
30  SanDisk 400GB Ultra microSDXC UHS-I Memory Car...  4.8 out of 5 stars   
31     Fujifilm Instax Mini, 10 sheet x 2 pack, White  4.6 out of 5 stars   
32  Xiaomi Wireless IP Home Security Camera,1080P ...  4.1 out of 5 stars   
33  Imou 4MP FHD 360 Degree Security Camera (White...  3.0 out of 5 stars   
34       AmazonBasics Carrying Case for GoPro - Small  4.6 out of 5 stars   
35  Fujifilm Instax Mini Film For Instax Mini 7 / ...  4.4 out of 5 stars   
36  YI Dome Camera 1080p HD Wireless IP Security S...  4.5 out of 5 stars   
37  SanDisk Extreme 128GB SDXC Memory Card up to 1...  4.8 out of 5 stars   
38  Portable Universal Tripod Stand Adjustable For...  2.3 out of 5 stars   
39  GoPro Rechargeable Battery for HERO9 Black, AD...  4.7 out of 5 stars   
40  Sandisk Extreme microSDXC 128GB Plus SD Adapte...  4.8 out of 5 stars   
41  UGREEN 4K HDMI Cable High-Speed HDMI Cord Nylo...  4.8 out of 5 stars   
42                 OBD Vehicle Inspection Wifi Device  3.0 out of 5 stars   
43  AmazonBasics High-Speed Mini-HDMI to HDMI TV A...  4.4 out of 5 stars   
44  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
45  SAMSUNG EVO Select Plus Micro SD Memory Card +...  4.6 out of 5 stars   
46  AmazonBasics DisplayPort to HDMI Display Adapt...  4.1 out of 5 stars   
47  SanDisk 128GB Ultra MicroSDXC UHS-I Memory Car...  4.8 out of 5 stars   
48  AMINAC Star Night Light Projector, LED Star Pr...  5.0 out of 5 stars   
49  DR-E12 USB Power Kit DC Coupler Dummy Battery ...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.6        315           

# Best Sellers in Binoculars, Telescopes & Optics (Page 1) 

In [63]:
url ="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966400031/ref=zg_bs_nav_2_16966385031"


In [64]:
response = requests.get(url)
response.status_code

200

In [65]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [66]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [67]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [68]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.2 out of 5 stars\n'

In [69]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [70]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

GTHUNDER Digital Night Vision Goggles Binoculars for Total Darkness—Infrared Digital Night Vision Large Viewing Screen, 32GB Memory Card for Photo and Video Storage—Perfect for Surveillance
4.3 out of 5 stars
4.3
1,791
1791
SAR 760.00
760.00


In [71]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [72]:
products_df5 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df5

pro_name            pro_rate  \
0   GTHUNDER Digital Night Vision Goggles Binocula...  4.3 out of 5 stars   
1   (Single Pack) - Carson MicroBrite Plus 60 -120...  4.2 out of 5 stars   
2                          Apple Pencil Tips - 4 pack  4.8 out of 5 stars   
3   Bushnell Falcon Binoculars 7x35 mm # 133410 - ...  4.5 out of 5 stars   
4   Bushnell Falcon 10x50 Wide Angle Binoculars - ...  4.5 out of 5 stars   
5        Celestron Portable Telescope Travel Scope 70  4.3 out of 5 stars   
6     2.1X Eschenbach Max TV Glasses Distance Viewing                 NaN   
7   10X25 Small Compact Lightweight Binoculars for...  3.3 out of 5 stars   
8   16X52 Monocular Telescope, High Power Prism Co...                 NaN   
9   Telescope, 70mm Aperture 400mm AZ Mount Astron...                 NaN   
10  Celestron – Outland X 8x42 Binoculars – Waterp...  4.5 out of 5 stars   
11        Steiner 5845 7X50 Sagor II Binocular, Green  5.0 out of 5 stars   
12  Phone JJone APL-JS60XJJ09 Metal 60X HD Phone T...                 NaN   
13  Celestron UpClose G2 10x25 Monocular, Black (7...  4.0 out of 5 stars   
14  Telescope Phone Mount, Universal Smart Phone A...  3.5 out of 5 stars   
15  Universal Bino Binocular Tripod Mount Adapter ...  4.4 out of 5 stars   
16  National Geographic 50Mm Telescope For Kids by...  3.7 out of 5 stars   
17                        PROFESSIONAL COOLING SYSTEM  5.0 out of 5 stars   
18                   Bushnell Trophy Xtreme Binocular  4.6 out of 5 stars   
19              Bushnell 10x42 Binocular منظار بوشنيل  3.4 out of 5 stars   
20  Docooler Lens Telescope 16x52 Telescope Monocu...                 NaN   
21  40X60 HD Mini Day and Night Vision Monocular T...  3.1 out of 5 stars   
22  Celestron - 70mm Travel Scope DX - Portable Re...  4.2 out of 5 stars   
23           Celestron 21039 PowerSeeker 50 Telescope  4.1 out of 5 stars   
24  ComCreate 8X Folding High Powered Binoculars W...  1.0 out of 5 stars   
25  Steiner Peregrine Binoculars, Perfect for Wild...  4.2 out of 5 stars   
26       Celestron 93230 8 to 24mm 1.25 Zoom Eyepiece  4.7 out of 5 stars   
27  Jiusion 40 to 1000x Magnification Endoscope, 2...  4.2 out of 5 stars   
28  Celestron 93529 X-Cel LX 1.25-Inch 2x Barlow L...  4.7 out of 5 stars   
29  Garberiel Monocular Telescope 12X50 High Power...  1.7 out of 5 stars   
30  Nikon BAA807SB Fernglas Aculon A30 8x25 Binocu...  4.5 out of 5 stars   
31  Celestron 21045 PowerSeeker 114EQ Telescope - ...  4.1 out of 5 stars   
32  Celestron - PowerSeeker 127EQ Telescope - Manu...  4.2 out of 5 stars   
33  Nikon 7246 Action 12x50 EX Extreme All-Terrain...  4.6 out of 5 stars   
34             Steiner 8X30 Sagor II Binocular, Green  5.0 out of 5 stars   
35  8x21 Kids Binoculars Set - High Resolution Rea...  4.0 out of 5 stars   
36  Celestron 93428 X-Cel LX 1.25-Inch 3x Barlow L...  4.6 out of 5 stars   
37  Baigaish Binocular 20x50 HD Professional/Water...                 NaN   
38    Celestron StarSense Explorer DX 130AZ Telescope  4.3 out of 5 stars   
39  NATIONAL GEOGRAPHIC Junior Metal Detector –Adj...  4.2 out of 5 stars   
40      Sunagor Mega Zoom Binoculars 30-160x70 ,Black  3.7 out of 5 stars   
41  Sunagor Compact Zoom Binoculars 25-110x30,Silv...  3.7 out of 5 stars   
42  Panasonic P-6JRC Replacement Water Filter Cart...  4.6 out of 5 stars   
43                        Celestron 1.25" Moon Filter  4.1 out of 5 stars   
44      Bushnell Legend Ultra HD Roof Prism Binocular  4.6 out of 5 stars   
45  Celestron - 50mm Travel Scope - Portable Refra...  3.8 out of 5 stars   
46  Built in Motion Plus Remote and Nunchuck Contr...                 NaN   
47  HEXEUM Night Vision Goggles Night Vision Binoc...  4.6 out of 5 stars   
48  10X22 Binocular Telescope Night Version Foldab...  2.8 out of 5 stars   
49  Celestron - SkyMaster 25x70 Binocular - Large ...  4.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.3      1,791           

# Best Sellers in Binoculars, Telescopes & Optics (Page 2)

In [73]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966400031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [74]:
response = requests.get(url)
response.status_code

200

In [75]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [76]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [77]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [78]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.4 out of 5 stars\n'

In [79]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [80]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Telescope Star Finder with Tripod F36050 HD Zoom Monocular Space Astronomical Spotting Scope for Kids and Beginner (Small)
3.3 out of 5 stars
3.3
841
841
SAR 216.54
216.54


In [81]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [82]:
products_df6 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df6

pro_name            pro_rate  \
0   Telescope Star Finder with Tripod F36050 HD Zo...  3.3 out of 5 stars   
1   HUTACT 10x42 Binoculars for Adults, with Stora...  4.4 out of 5 stars   
2   SCOKC Binoculars 20x50 High Power, Compact HD ...  4.7 out of 5 stars   
3   DMG-Digital Microscope 50x To 1000x Magnificat...  3.0 out of 5 stars   
4   12X50 HD Monocular Telescope with Quick Smartp...                 NaN   
5   ARCTIC P12 PWM (Black/Black) - Pressure-optimi...  4.6 out of 5 stars   
6   Gskyer Telescope, 70mm Aperture 400mm AZ Mount...  4.4 out of 5 stars   
7   Bysameyee USB Digital Microscope 40X to 1000X,...  3.0 out of 5 stars   
8   Newdoar 25x30 Zoomable Monocular Vintage Pirat...  4.2 out of 5 stars   
9   Camera Diaphragm, Compact Iris Aperture Adjust...                 NaN   
10  12x42 Binoculars for Adults with New Smartphon...  4.8 out of 5 stars   
11  Mega Sports 10X25 Compact Binocular for Bird W...                 NaN   
12  Carson MicroFlip 100x-250x LED Lighted Pocket ...  4.1 out of 5 stars   
13           Nikon Aculon A211 7x50 Binoculars, Black  4.6 out of 5 stars   
14  SCOKC 10x-20x Zoom Binoculars Monocular HD Pow...  4.3 out of 5 stars   
15  2021 Newest Telescope, 60mm Aperture 500mm AZ ...                 NaN   
16  Celestron - NexStar 127SLT Computerized Telesc...  4.3 out of 5 stars   
17             10X42 Darbel Bushnell Sport Roof Prism  3.6 out of 5 stars   
18                 Vortex Optics Solo Monocular 10x25  4.4 out of 5 stars   
19  10x34 glasses type low light night vision tele...  2.4 out of 5 stars   
20  NIKULA metal High powered telescope zoom porta...  1.6 out of 5 stars   
21  Celestron Upclose 20x50 Binoculars Porro Prism...  4.0 out of 5 stars   
22  Celestron – Outland X 10x50 Binoculars – Water...  4.5 out of 5 stars   
23                Opticron BGA 10x42 Monocular, black  4.7 out of 5 stars   
24  Celestron 93524 Roof and Porro Binocular Tripo...  4.3 out of 5 stars   
25  SOOBA Astronomical Telescope Compact Portable ...                 NaN   
26  Steiner Marine Binoculars for Adults and Kids,...  4.8 out of 5 stars   
27  Celestron - PowerSeeker 70AZ Telescope - Manua...  4.2 out of 5 stars   
28  8"x8" Solar Filter Sheet for Telescopes, Binoc...                 NaN   
29   Bushnell Monoculars Telescope 16x52 Lens - Black  3.1 out of 5 stars   
30             قاعدة تصوير دربيل او ناظور صيد احترافي                 NaN   
31  Steiner 4477 10X26 Safari Ultrasharp Binocular...  4.5 out of 5 stars   
32  Balacoo Monocular Telescope 40x60 High Definit...                 NaN   
33  ARCTIC ACFAN00135A P12 Value Pack - Pressure-O...  4.6 out of 5 stars   
34  Bushnell Equinox Z Night Vision 6X50 EQUINOX Z...  4.0 out of 5 stars   
35  KA Monocular Telescope fo Phone, 40X60 HD Mono...                 NaN   
36  Celestron - PowerSeeker Telescope Accessory Ki...  4.6 out of 5 stars   
37   Celestron 93317 Omni Series 1.25" (6mm) Eyepiece  4.6 out of 5 stars   
38  10x22 Binoculars Professional Telescope Zoom V...                 NaN   
39  12X50 Powerful Binoculars, High Power HD Binoc...  4.3 out of 5 stars   
40  Celestron - Cometron 7x50 Bincoulars - Beginne...  4.6 out of 5 stars   
41         Panda 35x50 Adjustable Monocular Telescope  2.9 out of 5 stars   
42                 Steiner Military-Marine Binoculars  4.6 out of 5 stars   
43  Binoculars for Kids - HIGH Resolution, Shockpr...  4.5 out of 5 stars   
44  Astronomy Refractor Telescope, High Definition...                 NaN   
45  Joshjt Telescope 70mm Aperture 400mm AZ Mount,...                 NaN   
46  National Geographic 90-01001 50/600 Refractor ...  3.8 out of 5 stars   
47  Bushnell Powerview Compact Folding Roof Prism ...  4.3 out of 5 stars   
48  60X60 Binoculars Telescope, Night Vision 10000...                 NaN   
49  Scienish Telescope Travel Scope 90 X Refractor...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.3        841           

# Best Sellers in Computers, Components & Accessories (Page 1)

In [83]:
url= " https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966388031/ref=zg_bs_nav_1_electronics"

In [84]:
response = requests.get(url)
response.status_code

200

In [85]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [86]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [87]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [88]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [89]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [90]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Stylus Pen for iPad with Palm Rejection, Active Pencil Compatible with (2018-2021) iPad Pro 11 & 12.9 inch, iPad 9th/8th/7th/6th Gen, iPad Air 4th/3rd Gen,iPad Mini 6th/5th Gen
3.4 out of 5 stars
3.4
5,548
5548
SAR 58.75
58.75


In [91]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [92]:
products_df7 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df7

pro_name            pro_rate  \
0   Stylus Pen for iPad with Palm Rejection, Activ...  3.4 out of 5 stars   
1   530pcs/set Heat Shrink Tubing Insulation Shrin...  4.1 out of 5 stars   
2   UGREEN USB C Cable 2M, Braided 100W Power Deli...  4.2 out of 5 stars   
3   Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
4   TP-Link AC1750 Wi-Fi Range Extender - RE450, W...  4.0 out of 5 stars   
5   Glorious Large Gaming Mouse Pad 11''x13'' - Black  4.7 out of 5 stars   
6   Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
7   Razer Seiren Mini - USB Condenser Microphone f...  4.6 out of 5 stars   
8   Kingston A400 SATA SSD Solid State Drive 2.5 I...  4.5 out of 5 stars   
9   SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal ...  4.8 out of 5 stars   
10  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
11  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
12  MSI MPG Z490 Gaming Plus Gaming Motherboard (A...  4.6 out of 5 stars   
13  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
14  YISK Store Extended Large Gaming Mouse Pad XL ...  4.2 out of 5 stars   
15  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
16  ZORD PHANTOM-1 GAMING PC, RYZEN 3 3200G, 16GB ...  3.3 out of 5 stars   
17  Thermal Grizzly Kryonaut 12.5 W / m · K 1 g th...  4.7 out of 5 stars   
18  Seagate BarraCuda 4TB Internal Hard Drive HDD ...  4.7 out of 5 stars   
19  HP 652 Ink Advantage Cartridge, Tri-color - F6...  4.4 out of 5 stars   
20  SAMSUNG 970 EVO Plus SSD 2TB - M.2 NVMe Interf...  4.9 out of 5 stars   
21  SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
22  Large Gaming Mousepad World Map Game Mouse Pad...  4.2 out of 5 stars   
23  TP-Link AC1200 Whole-Home Mesh Wi-Fi System(DE...  4.2 out of 5 stars   
24  Desk, Laptop Desk Bed Foldable Lazy Small Tabl...  3.9 out of 5 stars   
25  2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
26  Logitech C922 Pro Stream Webcam, HD 1080p/30fp...  4.6 out of 5 stars   
27  Fasgear USB C Cable for Oculus Quest Link 2, 9...  4.0 out of 5 stars   
28  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
29         Anker Powerline+ II 6 Foot Lightning Cable  4.1 out of 5 stars   
30  ProCase iPad Air 4 Screen Protector 10.9 2020/...  4.6 out of 5 stars   
31  Linksys WAP1200AC WiFi Access Point (AC1200 Si...  3.3 out of 5 stars   
32  SanDisk SSD PLUS 1TB - 2.5” SATA SSD, up to 53...  4.7 out of 5 stars   
33  Stylus Pen for Touch Screens and Phone, Rechar...  3.8 out of 5 stars   
34    Kioxia Exceria 64GB MicroSD Card - LMEX1L064GG2  4.6 out of 5 stars   
35    HP 652 Ink Advantage Cartridge, Black - F6V25AE  4.4 out of 5 stars   
36  UGREEN iPhone Lightning Cable 2M [MFi Certifie...  4.6 out of 5 stars   
37  SanDisk SSD PLUS 240GB - 2.5” SATA SSD, up to ...  4.7 out of 5 stars   
38                     ZORD M27 GAMING MONITOR 27INCH  3.8 out of 5 stars   
39          SanDisk Cruzer Blade USB Flash Drive 64GB  4.5 out of 5 stars   
40  Samsung Electronics A7 Tablet 10.4 Wi-Fi 64GB ...  4.1 out of 5 stars   
41  Stylus Pen for iPad with Palm Rejection, Activ...  4.6 out of 5 stars   
42  AmazonBasics Braided 4K HDMI to HDMI Cable - 3...  4.7 out of 5 stars   
43  Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
44  Acer KG241QS - 23.6" (Full HD)1920 x 1080 over...  4.4 out of 5 stars   
45  AmazonBasics USB 2.0 A-Male to Micro B Charger...  4.5 out of 5 stars   
46  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
47  Toshiba 1TB Canvio Basics Portable USB3.0 Hard...  4.6 out of 5 stars   
48  Logitech G PRO X Gaming Headset 2nd Generation...  4.5 out of 5 stars   
49  TKOOFN Large RGB Colorful LED Light Keyboard M...  3.8 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.4      5,548           

 # Best Sellers in Computers, Components & Accessories (Page 2)

In [93]:
url ="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966388031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [94]:
response = requests.get(url)
response.status_code

200

In [95]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [96]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [97]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [98]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.5 out of 5 stars\n'

In [99]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [100]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

3Pack Original [Apple MFi Certified] Charger Lightning to USB Cable Compatible iPhone 11 Pro/11/XS MAX/XR/8/7/6s/6/plus,iPad Pro/Air/Mini,iPod Touch(White 1M/3.3FT)
4.5 out of 5 stars
4.5
4,135
4135
SAR 60.00
60.00


In [101]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [102]:
products_df8 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df8

pro_name            pro_rate  \
0   3Pack Original [Apple MFi Certified] Charger L...  4.5 out of 5 stars   
1   SteelSeries Arctis 7 - Lossless Wireless Gamin...  4.5 out of 5 stars   
2   4 Pack Cable Management Sleeve, Cord Organizer...  4.2 out of 5 stars   
3   SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
4   Samsung Electronics (MZ-V8V1T0B/AM) 980 SSD 1T...  4.7 out of 5 stars   
5   UGREEN iPhone Lightning Cable [MFi Certified] ...  4.1 out of 5 stars   
6   UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
7   [2 Pack] ProCase Screen Protector for Galaxy T...  3.8 out of 5 stars   
8   UGREEN iPhone 13 Charger Cable [MFi Certified]...  4.1 out of 5 stars   
9   HyperX QuadCast - USB Condenser Gaming Microph...  4.8 out of 5 stars   
10  Western Digital WDS500G2B0A WD Blue 3D NAND In...  4.7 out of 5 stars   
11  WD 5TB My Passport Portable External Hard Driv...  4.2 out of 5 stars   
12  iPhone Charger Lightning Cable 10ft - by TalkW...  4.1 out of 5 stars   
13  Anti-Skid Mousepad Extended Super Large World ...  4.0 out of 5 stars   
14  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
15  USB C 9-in1 Hub with 4K HDMI Adapter 100W PD C...  4.4 out of 5 stars   
16  EXCOVIP Extended Large Gaming Mouse Pad XXL (9...  4.5 out of 5 stars   
17  Epson EcoTank L3150 Print/Scan/Copy Wi-Fi Tank...  3.7 out of 5 stars   
18  TP-Link AC1300 USB WiFi Adapter(Archer T3U)- 2...  4.5 out of 5 stars   
19  YEFOOT iPhone Charger [MFi Certified] 6Pack[3/...  4.4 out of 5 stars   
20  HP 123 Black Original Ink Advantage Cartridge ...  4.1 out of 5 stars   
21  Logitech Z150 Compact Multimedia Stereo Speake...  4.4 out of 5 stars   
22  UGREEN SD Card Reader USB 3.0/USB C OTG Dual S...  4.5 out of 5 stars   
23  WD Blue SN550 500GB NVMe Internal SSD - Gen3 x...  4.6 out of 5 stars   
24  New Office 2021 Pro For Windows | Lifetime Act...  5.0 out of 5 stars   
25  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.9 out of 5 stars   
26  Asus Gaming Monitor - 27inch, Full HD, 0.5ms, ...  4.6 out of 5 stars   
27  AMD Ryzen 9 5900X 12-core, 24-Thread Unlocked ...  4.8 out of 5 stars   
28  5-Socket Extension Cord with Individual on/off...  4.2 out of 5 stars   
29  SAMSUNG 870 QVO SATA III 2.5" SSD 1TB (MZ-77Q1...  4.8 out of 5 stars   
30  UGREEN USB 3.0 Hub 4 Port USB 3 Data Hub Porta...  4.5 out of 5 stars   
31  Precision Screwdriver Set,ShowTop 110 in 1 Mag...  3.8 out of 5 stars   
32  Memory Foam Wrist Rest Pad and Mouse Wrist Res...  3.8 out of 5 stars   
33  AccLoo Single Monitor Desk Mount Stand - Full ...  4.7 out of 5 stars   
34  iPhone Fast Charger Cable, 【Apple MFi Certifie...  1.0 out of 5 stars   
35  Anker Powerline Micro USB - Charging Cable, wi...  4.3 out of 5 stars   
36  UGREEN Metal Tablet Stand Mobile Phone Holder ...  4.6 out of 5 stars   
37  Corsair XTM50 High Performance Ultra-Low Therm...  4.7 out of 5 stars   
38  Corsair TM30 Performance Thermal Paste, Premiu...  4.7 out of 5 stars   
39  UGREEN USB C Cable 1M, Braided 100W Power Deli...  4.2 out of 5 stars   
40  SAMSUNG 980 PRO 1TB PCIe NVMe Gen4 Internal Ga...  4.8 out of 5 stars   
41  Laptop Stand, BiuLing Adjustable Portable Lapt...  3.6 out of 5 stars   
42  Cooler Master MWE Gold 750 V2 Full Modular, 75...  4.4 out of 5 stars   
43  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
44  Glorious Gaming Mouse Model O Minus - Matte White  4.3 out of 5 stars   
45  Dell Inspiron 5400 All In One Desktop Computer...                 NaN   
46          TP-LINK AC1200 Wi-Fi Range Extender RE305  4.1 out of 5 stars   
47  Mainstayae High Speed 4 Port USB 3.0 Multi HUB...  3.5 out of 5 stars   
48  UGREEN iPhone Charging Cable [Apple MFi Certif...  4.5 out of 5 stars   
49  AmazonBasics Apple Certified 30-Pin to USB Cab...  4.6 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.5      4,135           

# Best Sellers in Headphones, Earbuds & Accessories (Page 1 )

In [103]:
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966390031/ref=zg_bs_pg_1?ie=UTF8&pg=1"

In [104]:
response = requests.get(url)
response.status_code

200

In [105]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [106]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [107]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [108]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [109]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [110]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

New Apple Airpods Pro
4.3 out of 5 stars
4.3
2,355
2355
SAR 749.00
749.00


In [111]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [112]:
products_df9 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df9

pro_name            pro_rate  \
0                               New Apple Airpods Pro  4.3 out of 5 stars   
1                    Apple AirPods with Charging Case  4.1 out of 5 stars   
2                  New Apple AirPods (3rd generation)  4.4 out of 5 stars   
3   Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.8 out of 5 stars   
4   SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
5   Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
6   Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
7   Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
8                  JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
9                                   Apple AirPods Pro  4.3 out of 5 stars   
10  Bluetooth Wireless Headphones 40 Hours Playtim...  4.3 out of 5 stars   
11  Samsung Galaxy SM-R175 Wireless Buds Plus with...  4.2 out of 5 stars   
12  Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.3 out of 5 stars   
13  Sony WF-1000XM4 Industry Leading Noise Cancell...  3.9 out of 5 stars   
14  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
15  Anker Soundcore Life P2 Wireless Earbuds with ...  4.2 out of 5 stars   
16  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.0 out of 5 stars   
17  Sony MDR-ZX110AP Wired On-Ear Headphones with ...  4.1 out of 5 stars   
18  SoundPEATS Wireless Earbuds Bluetooth 5.0 Head...  3.9 out of 5 stars   
19  HyperX Cloud II Gaming Headset for PC & PS4 & ...  4.6 out of 5 stars   
20  Wired Lightning Headset Earphone for Apple iPh...  2.0 out of 5 stars   
21  Bose QuietComfort Earbuds - True Wireless Nois...  4.4 out of 5 stars   
22  JBL T110 Wired Universal In-Ear Headphone with...  4.2 out of 5 stars   
23    Apple Lightning to 3.5mm Headphone Jack Adapter  4.2 out of 5 stars   
24  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
25  Datazone Ear phone Headphones,crystal clear so...  3.6 out of 5 stars   
26  JBL TUNE115TWS True Wireless Earbuds Black, small  4.0 out of 5 stars   
27  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
28  Wireless Earbuds SOUNDPEATS Sonic in-Ear Wirel...  3.9 out of 5 stars   
29  Sony WF-C500 True Wireless Headphones - Up to ...  5.0 out of 5 stars   
30  Wireless Earbuds SoundPEATS T2 Hybrid Active N...  4.2 out of 5 stars   
31  Sony WH-CH510 Wireless Bluetooth On-Ear with M...  3.7 out of 5 stars   
32  UGREEN USB C to 3.5mm Headphone Jack Audio Cha...  4.1 out of 5 stars   
33  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.5 out of 5 stars   
34  Wireless Earbuds SoundPEATS TrueCapsule2 with ...  3.7 out of 5 stars   
35  Razer Kraken - Wired Gaming Headset for Multip...  4.4 out of 5 stars   
36  Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
37  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.1 out of 5 stars   
38  Joyroom JR-T03S TWS Bluetooth True Wireless St...  2.7 out of 5 stars   
39  JBL LIVE 500BT Wireless On-Ear Headphones with...  4.3 out of 5 stars   
40  SoundPEATS TrueFree2 Wireless Earbuds Bluetoot...  4.0 out of 5 stars   
41  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
42  Hybrid Active Noise Cancelling Headphones with...  4.8 out of 5 stars   
43  Joyroom JR-T03S In-Ear Detection True Wireless...  2.8 out of 5 stars   
44  Amoi F9 Bluetooth 5.0 Wireless Earbuds,IPX7 Wa...  2.8 out of 5 stars   
45  HUAWEI FreeBuds Studio Wireless Earphones, Int...  4.8 out of 5 stars   
46  SoundPEATS H1 Wireless Earbuds, Bluetooth V5.2...  4.0 out of 5 stars   
47  Wireless Earbuds, SoundPEATS T3 Active Noise C...  4.5 out of 5 stars   
48  Beats Studio Buds True Wireless Noise Cancelli...  3.5 out of 5 stars   
49    Huawei Sport lite Bluetooth Headset AM61, Black  4.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.3      2,355           

# Best Sellers in Headphones, Earbuds & Accessories (Page 2 )

In [113]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966390031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [114]:
response = requests.get(url)
response.status_code

200

In [115]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [116]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [117]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [118]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.7 out of 5 stars\n'

In [119]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [120]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Wireless Earbuds SoundPEATS TrueAir2 Bluetooth V5.2 Wireless Earphones with Qualcomm QCC3040, True-Wireless Mirroring, 4 Mics for Clear Calls and CVC 8.0 Noise Cancellation, aptX Codec, Total 25 Hours
3.8 out of 5 stars
3.8
2,095
2095
SAR 132.00
132.00


In [121]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [122]:
products_df10 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df10

pro_name            pro_rate  \
0   Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
1   Sony WH-CH510 Wireless Bluetooth On-Ear with M...  3.7 out of 5 stars   
2   ElloGear 2020 Earbuds Stereo Headphones for Sa...  4.0 out of 5 stars   
3   For iPhone X 8 7 Plus Bluetooth Earphones Wire...  2.5 out of 5 stars   
4           Nokia Lite Earbuds BH-205 - Black, Normal  3.3 out of 5 stars   
5   HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.4 out of 5 stars   
6   JOYROOM JR-T03s white Wireless bluetooth headp...  2.7 out of 5 stars   
7       TOSHIBA RZE-BT1200H Wireless Headphones Black  4.5 out of 5 stars   
8   SAMSUNG Galaxy Buds Pro, True Wireless Earbuds...  4.2 out of 5 stars   
9   TPU Silicone Case for AirPods Pro, Heavy Duty ...  3.5 out of 5 stars   
10  JBL Tune 120TWS True Wireless In-Ear Headphone...  4.0 out of 5 stars   
11  Sony MDREX15APBLACK Wired In-Ear Headphones EX...  3.9 out of 5 stars   
12  Anker Soundcore Life P2 Mini Bluetooth Earphon...  4.2 out of 5 stars   
13  SoundPEATS True Wireless Bluetooth Earbuds in-...  4.7 out of 5 stars   
14  Jabra Elite 75t Earbuds – Active Noise Cancell...  4.3 out of 5 stars   
15  TPU Silicone Case for AirPods 1/AirPods 2 , He...  3.5 out of 5 stars   
16  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.8 out of 5 stars   
17  HUAWEI BLUETOOTH HEADPHONE LITE AM61 MOONLIGHT...  4.3 out of 5 stars   
18  HONOR MOECEN True Wireless Stereo Earbuds, whi...  3.0 out of 5 stars   
19  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.1 out of 5 stars   
20  Redmi Airdots Black Bluetooth Earphones Youth ...  4.2 out of 5 stars   
21  Razer Hammerhead Duo - Stereo headset, durable...  3.9 out of 5 stars   
22  Huawei Stereo Earphones with Remote and Microp...  4.1 out of 5 stars   
23  Samsung Basic Mass Wired In Earphones, White -...  5.0 out of 5 stars   
24  Wirelss Earbuds SoundPEATS Mini Bluetooth V5.2...  4.2 out of 5 stars   
25  True Wireless Earphones, Bluetooth 5 earbuds w...  4.3 out of 5 stars   
26          JBL In-Ear Headphones, RED - T110, Normal  4.2 out of 5 stars   
27  HyperX Cloud II - Gaming Headset, 7.1 Surround...  4.0 out of 5 stars   
28  Bluetooth Earphones, SoundPEATS Dual Dynamic D...  4.2 out of 5 stars   
29  Lenovo Earphone Bluetooth5.0 Wireless Headset ...  3.1 out of 5 stars   
30  SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
31  UGREEN Wireless Earbuds HiTune Bluetooth 5.0 E...  4.3 out of 5 stars   
32  UGREEN USB-C to 3.5mm Adapter Full Compatibili...  4.2 out of 5 stars   
33             Astro A10 Headset Wired For PS4, Black  4.4 out of 5 stars   
34  F9-5B TWS Earphone with Power Bank Hifi True S...  3.5 out of 5 stars   
35  Wireless Earbuds SoundPEATS 100Hours Playtime ...  4.0 out of 5 stars   
36  Sennheiser M3IETW2 Momentum True Wireless 2 Bl...  5.0 out of 5 stars   
37  Wireless Earphones Bluetooth 5.0 SoundPEATS Q3...  4.2 out of 5 stars   
38  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.3 out of 5 stars   
39  Wireless Earbuds, Bluetooth v5.2 Headphones Mi...                 NaN   
40  Sony WF-1000XM3 True Wireless Noise Cancelling...  3.8 out of 5 stars   
41  New bee Bluetooth Earpiece V5.0 Wireless Hands...  4.1 out of 5 stars   
42  AirPods Pro Case Cover Silicone Protective Cas...  4.5 out of 5 stars   
43  beats Flex – All-Day Wireless Earphones – beat...  3.4 out of 5 stars   
44  UGREEN In-ear Headphone USB-C Earphone with Mi...  4.1 out of 5 stars   
45  HUAWEI FreeBuds 4 Wireless Bluetooth Open-fit ...  4.1 out of 5 stars   
46  Sony WI-XB400 Wireless Extra Bass in-Ear Headp...  3.7 out of 5 stars   
47  Razer Kraken X: Ultralight Gaming Headset: 7.1...  4.4 out of 5 stars   
48  HUAWEI FreeBuds Pro Bluetooth Wireless Earphon...  4.4 out of 5 stars   
49  For AirPods Pro Case, Shockproof Case for For ...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             3.8      2,095             

# Best Sellers in Mobile Phones & Communication Products (Page 1 )

In [123]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966387031/ref=zg_bs_nav_1_electronics"

In [124]:
response = requests.get(url)
response.status_code

200

In [125]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [126]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [127]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [128]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.0 out of 5 stars\n'

In [129]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [130]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)
4.1 out of 5 stars
4.1
40
40
SAR 499.00
499.00


In [131]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [132]:
products_df11 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df11

pro_name            pro_rate  \
0   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.1 out of 5 stars   
1   SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
2   Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
3                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
4   Samsung Galaxy A72 | Ultra High-Res Quad Camer...  4.2 out of 5 stars   
5   Apple iPhone 12 Pro With FaceTime (256GB) - Pa...  4.2 out of 5 stars   
6                               New Apple Airpods Pro  4.3 out of 5 stars   
7   Anker PowerCore Select 20000, 20000mAh Power B...  4.0 out of 5 stars   
8   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.2 out of 5 stars   
9   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.5 out of 5 stars   
10                   Apple AirPods with Charging Case  4.1 out of 5 stars   
11  Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
12  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
13  Anker Nano iPhone Charger, 20W PIQ 3.0 Durable...  4.2 out of 5 stars   
14  JBL Flip 5 Portable Speaker Waterproof Wireles...  4.6 out of 5 stars   
15  Apple iPhone 12 Pro With FaceTime (128GB) - Pa...  4.2 out of 5 stars   
16                 New Apple AirPods (3rd generation)  4.4 out of 5 stars   
17  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.8 out of 5 stars   
18  Apple Watch Series 6 (GPS, 44mm) - Blue Alumin...  4.6 out of 5 stars   
19  Xiaomi Redmi 9A Dual SIM, 32GB, 2GB RAM, 4G LT...  4.0 out of 5 stars   
20  SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
21  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
22      Apple iPhone 12 With FaceTime (128GB) - White  4.4 out of 5 stars   
23  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
24  UGREEN USB C Cable 2M, Braided 100W Power Deli...  4.2 out of 5 stars   
25  Xiaomi Redmi Note 10S, Dual SIM, 128GB, 6GB RA...  3.8 out of 5 stars   
26  Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
27  Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
28                 JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
29  Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
30  Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
31  Samsung Galaxy S21 5G | Pro Grade Triple Camer...  3.5 out of 5 stars   
32   New Apple iPhone 13 with FaceTime (256GB) - Blue  4.3 out of 5 stars   
33  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
34     Apple iPhone 12 With FaceTime (128GB) - Purple  4.4 out of 5 stars   
35                                  Apple AirPods Pro  4.3 out of 5 stars   
36  Anker PowerCore III 10K, Wireless Portable Cha...  4.7 out of 5 stars   
37  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.5 out of 5 stars   
38  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
39  Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
40     Apple iPhone 12 With FaceTime (256GB) - Purple  4.4 out of 5 stars   
41  Samsung Galaxy S20 FE 4G Android Smartphone, 1...                 NaN   
42  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
43  SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.1 out of 5 stars   
44  UGREEN 65W USB C Charger Plug 4 Port GaN Type ...  4.2 out of 5 stars   
45  Bluetooth Wireless Headphones 40 Hours Playtim...  4.3 out of 5 stars   
46  Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
47  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
48  Samsung Galaxy SM-R175 Wireless Buds Plus with...  4.2 out of 5 stars   
49  UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.1         40           

# Best Sellers in Mobile Phones & Communication Products (Page 2 )

In [133]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966387031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [134]:
response = requests.get(url)
response.status_code

200

In [135]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [136]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [137]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [138]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [139]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [140]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks Headphones Bluetooth 5.0 Stereo Sound Wireless Earphones with Touch Control IPX7 Waterproof for Sports, 12 mm Driver, USB-C Charge
4.3 out of 5 stars
4.3
192
192
SAR 103.20
103.20


In [141]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [142]:
products_df12 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df12

pro_name            pro_rate  \
0   Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.3 out of 5 stars   
1   Samsung Galaxy S20 FE Dual SIM - 128GB, 8GB RA...  4.1 out of 5 stars   
2        Apple iPhone 12 With FaceTime (128GB) - Blue  4.4 out of 5 stars   
3   UGREEN 2 Pack Screen Protector for iPhone 13/1...  4.4 out of 5 stars   
4   HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
5   Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
6   SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
7   UGREEN Clear iPhone 12/12Pro Case Compatible F...  4.1 out of 5 stars   
8   Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
9   Anker USB C Charger, 20W PIQ 3.0 Fast Charger ...  4.2 out of 5 stars   
10  UGREEN iPhone Charger PD20W USB C iPhone 13 Fa...  4.2 out of 5 stars   
11  Power Bank Portable Charger 10000mAh with cabl...  4.0 out of 5 stars   
12  Apple Watch Series 6 (GPS, 40mm) - Space Grey ...  4.6 out of 5 stars   
13  UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
14  Apple MagSafe Charger Qi/PMA for iPhone 13 Pro...  4.1 out of 5 stars   
15  Fasgear USB C Cable for Oculus Quest Link 2, 9...  4.0 out of 5 stars   
16  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
17  Sony WF-1000XM4 Industry Leading Noise Cancell...  3.9 out of 5 stars   
18  Samsung Galaxy A52s 5G Dual SIM Smartphone - 1...  4.6 out of 5 stars   
19        Apple iPhone 12 With FaceTime (64GB) - Blue  4.4 out of 5 stars   
20         Anker Powerline+ II 6 Foot Lightning Cable  4.1 out of 5 stars   
21  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
22  UGREEN iPhone Protective Case Compatible for i...  4.5 out of 5 stars   
23  Stylus Pen for Touch Screens and Phone, Rechar...  3.8 out of 5 stars   
24    Kioxia Exceria 64GB MicroSD Card - LMEX1L064GG2  4.6 out of 5 stars   
25  UGREEN iPhone Lightning Cable 2M [MFi Certifie...  4.6 out of 5 stars   
26  Samsung Galaxy S21 Dual SIM - 128GB, 8GB RAM, ...  3.5 out of 5 stars   
27  UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
28  Anker Soundcore Life P2 Wireless Earbuds with ...  4.2 out of 5 stars   
29  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.0 out of 5 stars   
30  Stylus Pen for iPad with Palm Rejection, Activ...  4.6 out of 5 stars   
31  Samsung EP-TA800 Travel Adapter for Super Fast...  4.3 out of 5 stars   
32   New Apple iPhone 13 with FaceTime (128GB) - Blue  4.3 out of 5 stars   
33  Xiaomi POCO X3 Pro, Dual SIM, 256GB, 8GB RAM, ...  4.2 out of 5 stars   
34  Sony MDR-ZX110AP Wired On-Ear Headphones with ...  4.1 out of 5 stars   
35  UGREEN 2 Pack Screen Protector for iPhone 12/1...  4.6 out of 5 stars   
36  JBL CLIP4 WIRELESS PORTABLE SPEAKER - Blue/Pin...  4.7 out of 5 stars   
37  Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
38  AmazonBasics USB 2.0 A-Male to Micro B Charger...  4.5 out of 5 stars   
39  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
40  UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
41  Travel Adapter,ShowTop Power Plug Adapter Inte...  3.9 out of 5 stars   
42  Apple iPhone 12 Pro With FaceTime (256GB) - Si...  4.2 out of 5 stars   
43  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.5 out of 5 stars   
44  SoundPEATS Wireless Earbuds Bluetooth 5.0 Head...  3.9 out of 5 stars   
45  3Pack Original [Apple MFi Certified] Charger L...  4.5 out of 5 stars   
46  New Apple iPhone 13 Pro Max with FaceTime (256...  4.5 out of 5 stars   
47  Milanese Loop Bracelet Stainless Steel band Fo...  4.3 out of 5 stars   
48                    Apple iPhone 11 (128GB) - Green  4.3 out of 5 stars   
49  Samsung Galaxy S20 FE 4G Android Smartphone, 1...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.3        192           

# Best Sellers in Wearable Technology (Page 1)

In [143]:
url= "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966397031/ref=zg_bs_pg_1?ie=UTF8&pg=1"

In [144]:
response = requests.get(url)
response.status_code

200

In [145]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [146]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [147]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [148]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.6 out of 5 stars\n'

In [149]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [150]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple Watch Series 6 (GPS, 44mm) - Space Grey Aluminium Case with Black Sport Band
4.6 out of 5 stars
4.6
307
307
SAR 1,349.00
1349.00


In [151]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [152]:
products_df13 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df13

pro_name            pro_rate  \
0   Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
1   Apple Watch Series 6 (GPS, 44mm) - Blue Alumin...  4.6 out of 5 stars   
2   Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
3   HUAWEI Band 6, All-day SpO2 Monitoring, 1.47" ...  4.4 out of 5 stars   
4   SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.1 out of 5 stars   
5   Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
6   HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
7   Apple Watch Series 6 (GPS, 40mm) - Space Grey ...  4.6 out of 5 stars   
8                       Fitbit-Inspire 2, Black/Black  4.5 out of 5 stars   
9   Milanese Loop Bracelet Stainless Steel band Fo...  4.3 out of 5 stars   
10  Apple Watch Series 6 (GPS, 40mm) - Blue Alumin...  4.6 out of 5 stars   
11  Apple Watch Series 7 (GPS, 41mm) - Starlight A...  5.0 out of 5 stars   
12  SoundPEATS Smart Watch for Women New Upgraded,...  3.0 out of 5 stars   
13  ibsun Wireless Charger, 3 in 1 Wireless Chargi...  4.1 out of 5 stars   
14  Smart Watch for Women, AGPTEK 1.69"(43mm) Smar...  3.7 out of 5 stars   
15  Xiaomi Band 5 Smart Fitness Bracelet Heart Rat...  4.5 out of 5 stars   
16  Xiaomi Mi Band 4 Smart Bluetooth Fitness Brace...  4.4 out of 5 stars   
17  Apple Watch Series 7 (GPS, 41mm) - Midnight Al...  5.0 out of 5 stars   
18  JETech Screen Protector Compatible Apple Watch...  3.8 out of 5 stars   
19  Xioami Mi Smart Band 6 Sports Smart Bracelet- ...  4.3 out of 5 stars   
20  Compatible Apple Watch Case 44mm with Screen P...  3.7 out of 5 stars   
21  SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
22  Fitbit Versa 3, Health & Fitness Smartwatch wi...  4.4 out of 5 stars   
23  Smart Watch, YCCORG Fitness Tracker with Heart...  3.8 out of 5 stars   
24                     Fitbit Charge 5,Graphite/Black  3.1 out of 5 stars   
25  HONOR Band 6, Model ARG-B39, 1.47" AMOLED Disp...  4.1 out of 5 stars   
26  Smart Watch for Women and Men,Fitness Tracker ...  3.0 out of 5 stars   
27  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
28  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
29                         Garmin Quickfit Watch Band  4.2 out of 5 stars   
30  Fitbit Versa 3,Soft Gold/Thistle, Small and La...  4.4 out of 5 stars   
31  Fitbit Ace 3, Activity Tracker for Kids 6+ wit...  4.4 out of 5 stars   
32  GEEAN Silicone Watch Band Sport Watch Strap fo...  3.7 out of 5 stars   
33  24HOCL Smart Watch with 1.69'' Full Touch Scre...  4.1 out of 5 stars   
34  24HOCL Smart Watch for Kids Girls Boys, Activi...  5.0 out of 5 stars   
35  Fitbit Sense, Advanced Smartwatch with Tools f...  4.2 out of 5 stars   
36  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
37  Compatible with Apple Watch Bands 44mm 42mm, A...  3.8 out of 5 stars   
38  GEEAN Tempered Glass Screen Protector Case for...  3.8 out of 5 stars   
39  Smart Watch, Necomi ساعة ذكية, Fitness Tracker...  4.5 out of 5 stars   
40  GEEAN Silicone Watch Band Sport Watch Strap fo...  3.7 out of 5 stars   
41  Smárt Watches - HW22 Plus Smárt Watch Women 1....  3.7 out of 5 stars   
42  Compatible with HUAWEI Samsung Watch Silicone ...  3.7 out of 5 stars   
43  Smart Watch,Fitness Watch Cardio Exercise Hear...  3.5 out of 5 stars   
44  Compatible with Apple Watch Band, Nylon Strap ...  5.0 out of 5 stars   
45  Stylish Breathable with holes sport silicone w...  5.0 out of 5 stars   
46  Compatible with Apple Watch Band 40mm 38mm, Ad...  3.8 out of 5 stars   
47  [2-Pack] for Huawei Watch GT2 46mm Screen Prot...  3.9 out of 5 stars   
48  OIATROE Case with Tempered Glass Screen Protec...                 NaN   
49  HUAWEI WATCH FIT Elegant Smartwatch, Stainless...  4.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.6        307           

# Best Sellers in Wearable Technology (Page 2)

In [153]:
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966397031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [154]:
response = requests.get(url)
response.status_code

200

In [155]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [156]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [157]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [158]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.7 out of 5 stars\n'

In [159]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [160]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple Watch Magnetic Charging Cable (1 m)
3.0 out of 5 stars
3.0
1
1
SAR 99.00
99.00


In [161]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [162]:
products_df14 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df14

pro_name            pro_rate  \
0           Apple Watch Magnetic Charging Cable (1 m)  3.0 out of 5 stars   
1   HUAWEI WATCH FIT Elegant Smartwatch, Stainless...  4.7 out of 5 stars   
2   hw22 plus Smart Watch series 6 Bluetooth Call ...  2.4 out of 5 stars   
3   Apple Watch Series 7 (GPS, 45mm) - Starlight A...  5.0 out of 5 stars   
4           Smart Watch 42mm Midnight Blue Sport Band  2.8 out of 5 stars   
5   GEEAN Stainless Steel Watch Band Metal Strap f...  4.1 out of 5 stars   
6   OMIRA Smart Watch, Fitness Tracker with Heart ...  3.8 out of 5 stars   
7   EURCRBU Compatible with HUAWEI Watch GT, SAMSU...                 NaN   
8   Skullcandy Dime True Wireless Earbuds with 12 ...  4.1 out of 5 stars   
9   Jsbaby Smart Watch for Kids,Kids Smart Watch W...                 NaN   
10  Compatible with HUAWEI Samsung Watch Soft Sili...  3.3 out of 5 stars   
11  Xiaomi Mi Smart Watch Lite Black- 1.4 Inch Tou...  4.2 out of 5 stars   
12  elago MS5 Duo Charging Stand Compatible with M...  4.7 out of 5 stars   
13  MAZTRON 6-Pack Silicone Band Compatible with A...  4.5 out of 5 stars   
14  Screen Protector Compatible with Huawei Watch ...  3.2 out of 5 stars   
15      Charger For Huawei Watch GT Honor white color  4.3 out of 5 stars   
16  Apple Watch Series 7 (GPS + Cellular, 45mm) - ...                 NaN   
17  Leather loop strap For Apple watch band 44 mm ...  3.1 out of 5 stars   
18  Adjustable Woven replacement bands Compatible ...  4.0 out of 5 stars   
19  EZCO 2-Pack Screen Protector Case Compatible w...  4.0 out of 5 stars   
20  Compatible with Apple Watch Case with Screen P...  3.4 out of 5 stars   
21  Matte Case for Apple Watch 7 41mm 45mm, Hard P...  5.0 out of 5 stars   
22  Apple Watch Series 7 (GPS, 45mm) - Midnight Al...  4.6 out of 5 stars   
23  Black Breathable with holes sport silicone wat...  4.2 out of 5 stars   
24  Replacement Band for Apple Watch 38-40mm All S...  3.6 out of 5 stars   
25  OIATROE 2 Pack Tempered Glass Screen Protector...  1.6 out of 5 stars   
26  LWEN VR Headsets Compatible with iPhone & Andr...                 NaN   
27  VR Headset,VR Glasses,Virtual Reality Headset,...  1.0 out of 5 stars   
28  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
29  Smart Watch,Fitness Watch Cardio Exercise Hear...  5.0 out of 5 stars   
30  Compatible with Apple Watch Band 45mm 44mm 42m...  4.1 out of 5 stars   
31  HUAWEI HW-TIA-B09-PINK WATCH FIT Smartwatch wi...  4.5 out of 5 stars   
32  Apple Watch Magnetic Charger to USB-C Cable (0...                 NaN   
33  Case for Apple Watch 7 45mm Soft Slim TPU All ...  3.0 out of 5 stars   
34  Smart Watch,Handfree Bluetooth Call Smartwatch...                 NaN   
35  Samsung Galaxy Watch3 Stainless BT 45mm, Black...  4.3 out of 5 stars   
36  Compatible with Huawei Watch Fit Silicone Smar...                 NaN   
37  Adjustable Nylon Watch Band Compatible for App...  4.0 out of 5 stars   
38  Choco&Man US Diesel Retro Calfskin Genuine Lea...                 NaN   
39  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
40  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
41  Compatible with Apple Watch band 44mm, Watch S...  3.4 out of 5 stars   
42  Apple Watch Series 7 (GPS, 45mm) - Green Alumi...  5.0 out of 5 stars   
43  OROBAY Compatible with Apple Watch Band 45mm 4...  4.3 out of 5 stars   
44  Apple Watch Series 6 (GPS + Cellular, 40mm) - ...  4.2 out of 5 stars   
45  Coho Fit for Huawei Watch GT Bands 46mm, Samsu...  3.5 out of 5 stars   
46  Compatible with Apple Watch elastic band 42/44...  2.3 out of 5 stars   
47  Xiaomi Mi Smart Watch Lite Navy Blue- 1.4 Inch...  4.3 out of 5 stars   
48  TPU Protective Cover For Honor Watch ES Case F...  3.0 out of 5 stars   
49  Nylon Band Compatible with Huawei Watch Fit, L...  3.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.0          1           

# Best Sellers in Car & Vehicle Electronics (Page 1)

In [163]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966386031/ref=zg_bs_nav_1_electronics"

In [164]:
response = requests.get(url)
response.status_code

200

In [165]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [166]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [167]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [168]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.4 out of 5 stars\n'

In [169]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [170]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN Fast Car Charger Adapter 42.5W Dual USB Quick Charge QC 3.0 and PD Fast Charging Car Plug for iPhone 13 Pro/13 Pro Max/13/13 mini/12 Pro Max/11Pro Max,New iPad 9,iPad mini 6,Galaxy S20 S10,etc
4.3 out of 5 stars
4.3
2,192
2192
SAR 63.20
63.20


In [171]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [172]:
products_df15 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df15

pro_name            pro_rate  \
0   UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
1   UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
2   UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
3   UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
4   UGREEN Car Phone Holder Air Vent Cell Phone Mo...  4.3 out of 5 stars   
5                         ANKER POWERDRIVE 2 QC BLACK  3.9 out of 5 stars   
6   UGREEN Bluetooth Aux Adapter, Bluetooth 5.0 Au...  4.5 out of 5 stars   
7   UGREEN Car Phone Holder Magnetic Dashboard Mob...  4.2 out of 5 stars   
8   UGREEN Car Air Vent Mount Cell Phone Holder Gr...  4.4 out of 5 stars   
9   Muson Car Phone Mount, Dashboard/Air Vent/Wind...  3.7 out of 5 stars   
10  Anker Power Drive 2 24W 2 Port Car Charger For...  4.2 out of 5 stars   
11  UGREEN Magnetic Car Mount Dashboard Cell Phone...  4.1 out of 5 stars   
12  UGREEN Bluetooth Aux Adapter Bluetooth Car Rec...  4.4 out of 5 stars   
13  AccLoo Wireless Car Charger, 15W Qi Fast Charg...  5.0 out of 5 stars   
14  UGREEN Fast Car Charger Set with USB C Cable Q...  4.4 out of 5 stars   
15  Tekpatt Car Phone Holder, Universal Air Vent C...  3.5 out of 5 stars   
16  Belkin USB-C PD Car Charger 36W (Dual 18W USB-...  4.6 out of 5 stars   
17  UGREEN Magnetic Car Mount Phone Holder Univers...  4.2 out of 5 stars   
18  Go-Des Mini Strip Car Mount, Universal Mobile ...  4.5 out of 5 stars   
19  UGREEN Bluetooth Receiver for Car, Portable Wi...  4.0 out of 5 stars   
20  UGREEN Bluetooth 5.0 Adapter Car Bluetooth V5....  4.2 out of 5 stars   
21  70mai A500S Pro Plus+, 2K Front and Interior, ...                 NaN   
22  Tekpatt Gravity Car Phone Holder, Universal Ai...  4.5 out of 5 stars   
23          Belkin Magnetic Car Vent Mount V2 MagSafe  3.8 out of 5 stars   
24  UGREEN Bluetooth 5.0 Audio Transceiver Wireles...  3.8 out of 5 stars   
25  Baseus 360-degree Rotation Magnetic Mount Hold...  3.8 out of 5 stars   
26  UGREEN Fast Car Charger PD 40W Dual USB C Port...  4.3 out of 5 stars   
27  Huawei CP37 Type-C Car Charger with Super Char...  4.7 out of 5 stars   
28  UGREEN Car Headrest Mount Car Phone Mount Mobi...  4.1 out of 5 stars   
29  AccLoo Bluetooth FM Transmitter for Car,Blueto...  5.0 out of 5 stars   
30  Baseus Small Ears Series Magnetic Bracket（Vert...  4.4 out of 5 stars   
31  UGREEN Car Air Vent Mount Cell Phone Holder Gr...  4.4 out of 5 stars   
32  UGREEN Dashboard Car Phone Clip Holder Dash HU...  3.8 out of 5 stars   
33  Magnetic Phone Car Mount, WORLDMOM Strong Magn...                 NaN   
34  UGREEN Fast Car Charger 36W Dual USB QC 3.0 Qu...  4.3 out of 5 stars   
35  Bluetooth 5.0 Transmitter 2 in 1 Bluetooth Rec...  5.0 out of 5 stars   
36  15W Qi Wireless Fast Car Mount Charger, Auto D...  4.4 out of 5 stars   
37  UGREEN Portable Car Phone Holder Car Inverted ...  4.1 out of 5 stars   
38  UGREEN Car Phone Mount CD Slot Holder Gravity ...  4.0 out of 5 stars   
39  UGREEN Car Phone Mount Dashboard Clip Cell Pho...  3.4 out of 5 stars   
40  UGREEN Car Phone Holder for CD Slot Auto Lock ...  4.1 out of 5 stars   
41  Silicone Cover For Apple AirTag Case,AirTag Ke...                 NaN   
42  TLAXCA Wireless Car Charger, Intelligent Auto ...  5.0 out of 5 stars   
43  Promate Magnetic Car Mount Holder, Flexible Go...  4.5 out of 5 stars   
44  USB C Car Charger, Anker 33W PowerDrive PD＋ 2 ...  4.6 out of 5 stars   
45  Mobile Phone Holder for Car Mount, Durable Das...  4.3 out of 5 stars   
46  Car Phone Mount, Air Vent Cell Phone Holder fo...  4.1 out of 5 stars   
47  Car Phone Bracket 360-degree Rotation Foldable...  3.0 out of 5 stars   
48  Wireless Magnetic Car Charger, 15W Auto Clampi...                 NaN   
49  iOttie Easy One Touch 5 Dashboard & Windshield...  4.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.3      2,192             

# Best Sellers in Car & Vehicle Electronics (Page 2)

In [173]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966386031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [174]:
response = requests.get(url)
response.status_code

200

In [175]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [176]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [177]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [178]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'SAR 56.94'

In [179]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [180]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN Car Phone Holder Stand for Dashboard Adjustable Windshield Car Mobile Mount Dock Compatible with iPhone 13/13 mini/13Pro/13Pro Max/12/11 pro max/Galaxy S21 ultra A52 Huawei P30 Pro Mate 40 Pro
3.9 out of 5 stars
3.9
23
23
SAR 83.00
83.00


In [181]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [182]:
products_df16 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df16

pro_name            pro_rate  \
0   UGREEN Car Phone Holder Stand for Dashboard Ad...  3.9 out of 5 stars   
1   NNAA Vehicle Navigator Sunshade Visor GPS Navi...                 NaN   
2   Baseus T typed S-09A Bluetooth MP3 car charger...  4.3 out of 5 stars   
3   UGREEN Bike Phone Holder, Bicycle Motorcycle P...  4.3 out of 5 stars   
4   Universal Bluetooth Aux Music Receiver 3.5mm S...  2.4 out of 5 stars   
5   UGREEN Dashboard Phone Holder 360 Degree Car P...  3.6 out of 5 stars   
6   Bluetooth V2.0 7 Inch 2 DIN Car Video Stereo P...  3.1 out of 5 stars   
7   Universal Dashboard Car Mount Holder Rearview ...  3.0 out of 5 stars   
8   UGREEN Bluetooth FM Transmitter USB Car Fast C...  3.7 out of 5 stars   
9   LENCENT FM Transmitter, Bluetooth FM Transmitt...  4.4 out of 5 stars   
10  Car Headrest Mount Tablet Holder，ShowTop Unive...  4.0 out of 5 stars   
11  S5 Automatic Clamping Wireless Car Charger wit...  2.3 out of 5 stars   
12  CSN 15W Magnetic Wireless Car Charger Holder f...  2.6 out of 5 stars   
13  Fast C Type Charger Kit for Samsung Galaxy S21...  3.9 out of 5 stars   
14  Charger for Apple Watch, Travel Car Charger, P...  4.5 out of 5 stars   
15  Anker PowerDrive 2 24W 2-Port Car Charger- A23...  4.4 out of 5 stars   
16  SMAPRO Car Phone Holder, Car Mount for All Sma...  3.2 out of 5 stars   
17  Urise Car Phone Holder, 360° adjustable cup mo...  3.3 out of 5 stars   
18  UGREEN Car Phone Holder Gravity Air Vent Mount...  3.8 out of 5 stars   
19  Pioneer 1300W Bass Reflex Car Subwoofer With T...  4.4 out of 5 stars   
20  Belkin Boost Charge USB-C Fast Car Charger 20W...  4.5 out of 5 stars   
21  Car AUX Charging Cable Compatible with Mercede...  3.8 out of 5 stars   
22  Car Phone Mount, PHOCAR Universal Phone Holder...  2.8 out of 5 stars   
23  Car electric warmer mug (12v stainless steel d...  4.5 out of 5 stars   
24  24 Pieces Replacement Mount Metal Plates Unive...  4.5 out of 5 stars   
25  Wireless Bluetooth Receiver 3.5mm AUX Audio St...  3.4 out of 5 stars   
26  UGREEN Mini Car Charger Quick Charge 24W Dual ...  4.5 out of 5 stars   
27  Decdeal Car Phone Holder Rearview Mirror Mount...  2.8 out of 5 stars   
28  UGREEN Portable Car Phone Holder Car Cradle Au...  4.2 out of 5 stars   
29  Universal Smartphone Car Phone Holder Mount Cl...  3.0 out of 5 stars   
30  UGREEN Car Charger, Dual USB 24W/4.8A All Meta...  4.4 out of 5 stars   
31  Rapid Type C Car Charger, Compatible for Googl...  4.7 out of 5 stars   
32  MMOBIEL Speaker Set Left and Right Replacement...  4.1 out of 5 stars   
33  Carlinkit Wireless USB Carplay Dongle Adapter ...  3.2 out of 5 stars   
34  EZCase Air Vent Magnetic Car Mount Matte Finis...  4.4 out of 5 stars   
35  Wireless CarPlay Adapter U2W for Factory Wired...                 NaN   
36  Tekpatt Car Phone Holder, Universal Air Vent C...  5.0 out of 5 stars   
37  UGREEN Car Phone holder Car air Vent Gravity L...  4.0 out of 5 stars   
38  JUYUE Car Phone Holder Dashboard Cellphone Mou...  3.0 out of 5 stars   
39  Tycom Car Air Vent Mount Pigeon Cell Phone Hol...  5.0 out of 5 stars   
40  Magnetic Phone Holder for Car, WixGear [2 Pack...  4.4 out of 5 stars   
41         AMH Universal Magnetic Mobile Phone Holder  3.5 out of 5 stars   
42  Carg7 Universal Car MP3 FM Transmitter Modulat...  2.3 out of 5 stars   
43  GreenDesert Infrared induction automatic openi...                 NaN   
44  Morelian Ground Loop Noise Isolator Eliminatin...                 NaN   
45  Decdeal AMI MMI Audio Cable Aux Adapter BT Mus...  2.4 out of 5 stars   
46  GOMMLE Car Air Vent Mount, One-hand Operation ...  5.0 out of 5 stars   
47  4-in-1 Hands Free Wireless Bluetooth FM Transm...  1.7 out of 5 stars   
48  Fegishilly Car Charger with Dual USB, 3 Cigare...                 NaN   
49  2 Pack Mobile Phone Holder Car Mount Magnetic,...  3.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             3.9         23             

# Best Sellers in Electrical Power Accessories (Page 1)

In [183]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966395031/ref=zg_bs_nav_1_electronics"

In [184]:
response = requests.get(url)
response.status_code

200

In [185]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [186]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [187]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [188]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.0 out of 5 stars\n'

In [189]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [190]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple 20W USB-C Power Adapter, White
4.5 out of 5 stars
4.5
363
363
SAR 79.00
79.00


In [191]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [192]:
products_df17 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df17

pro_name            pro_rate  \
0                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
1   Extension Cord with 3 Power Socket and 3 USB S...  4.0 out of 5 stars   
2   FLIZIL Fast Charging Universal Travel Adapter,...  4.5 out of 5 stars   
3   Multi Extension Socket Plug Adapter with 3 USB...  4.6 out of 5 stars   
4   FLIZIL Lightning Cable, Apple MFi Certified Li...  4.5 out of 5 stars   
5   LDNIO SC3604 Socket extension, 6USB Ports 3.4A...  3.9 out of 5 stars   
6   FLIZIL Power Strip Extension with 4 way Socket...  4.5 out of 5 stars   
7   Belkin BSV804ar2M 8-Outlet Surge Protection Ex...  4.5 out of 5 stars   
8   5.6A Fast Charging Worldwide Travel Adapter Pl...  4.6 out of 5 stars   
9   Travel Adapter for KSA/UAE/UK, Plug for US/EU/...  4.4 out of 5 stars   
10  Belkin BSV603ar2M 6 Way/6 Plug 2m Surge Protec...  4.5 out of 5 stars   
11              Enriches electricity with 6 USB Ports  4.4 out of 5 stars   
12  3-Socket Extension Cord with Individual on/off...  3.9 out of 5 stars   
13             TVON POWER SOCKET 5M W/2USB TN-U6603-5  3.7 out of 5 stars   
14  Belkin BSV401ar2M 4-Outlet Surge Protection Ex...  4.5 out of 5 stars   
15  FLIZIL USB C Cable 3A Fast Charging Cable Nylo...  4.5 out of 5 stars   
16  Anself Intelligent Efficient Household 200W AC...  2.6 out of 5 stars   
17  Extension Cord with USB, Power Strip with 3 Ou...  3.7 out of 5 stars   
18  Travel Adaptor for KSA/US/UK/JP/CN/AU Plug Con...  3.2 out of 5 stars   
19  TOMSHOO Universal Travel Adapter 4 USB 2.4A Ch...  2.9 out of 5 stars   
20  LDNIO POWERFUL CHARGING SERISE Power Strip wit...  3.7 out of 5 stars   
21  Belkin BSV400ar2M 4 Way/4 Plug 2 m Surge Prote...  4.5 out of 5 stars   
22           Power connection of 2500 watts multi-use  4.0 out of 5 stars   
23  BXOE - Extension Lead Tower 12 Way, Power Stri...  5.0 out of 5 stars   
24          Extension Cord, 5 Meters, 4 Ports, German  4.9 out of 5 stars   
25          alfanar cord extension 13A with 4 ports 3  4.6 out of 5 stars   
26  Multi Plug Extension Sockets ，3 Way Multi Plug...                 NaN   
27  Wall Mounted USB Power Strip, NTONPOWER Multi ...  4.2 out of 5 stars   
28  KLARHEIT Upgraded Universal Travel Adapter One...  3.9 out of 5 stars   
29  Power Strip 1.8m Surge Protector Plug Extensio...  4.7 out of 5 stars   
30                          Socket Adapter 3 Way 7012  4.1 out of 5 stars   
31  HUACHEST Remote Control &Voice Control Smart p...  5.0 out of 5 stars   
32  Universal AU US EU to UK AC Power Plug Travel ...  3.4 out of 5 stars   
33  Brennenstuhl Extension Cord 3meter 6 sockets, ...  5.0 out of 5 stars   
34  BS8546 Approved KSA/UAE/UK to EU/DE/FR Adaptor...  4.6 out of 5 stars   
35  Double Socket Adapter with USB, 5V 2.1A USB Wa...  5.0 out of 5 stars   
36             4 Way Universal T-Socket Multi Adaptor  4.4 out of 5 stars   
37  Universal Power Adapter AC 100-240V DC 12V 2A ...  3.3 out of 5 stars   
38  Travel Adapter for KSA/UAE/UK, Plug for US/EU/...  4.4 out of 5 stars   
39  LENCENT 2X EU to UK Plug Adapter, Europe Schuk...  5.0 out of 5 stars   
40  2 Pack 20FT Power Extension Cable Compatible w...  4.7 out of 5 stars   
41  US/CA/JP Type B Adaptor Plug with Flat Blades/...  3.4 out of 5 stars   
42                  Power connection with 6 USB ports  3.3 out of 5 stars   
43  PHLIGHT Vertical Power Strip 2 layers, 7 outle...  3.9 out of 5 stars   
44             Terminator 3 Way Universal Plug Socket  4.1 out of 5 stars   
45  Socket extension, 6USB Ports with on/off Switc...  3.0 out of 5 stars   
46  DIGITPLUS - 3 Way Power Extension Cord with US...  2.5 out of 5 stars   
47  [2-Pack]US USA America/ Canada/ EU Europe Euro...                 NaN   
48  Intelligent Efficient Household 200W AC 220V T...  5.0 out of 5 stars   
49  MIMCO 12VDC, 2 Ampere Power Adapter — AC100V-2...  4.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.5        363             

# Best Sellers in Electrical Power Accessories (Page 2)

In [193]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966395031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [194]:
response = requests.get(url)
response.status_code

200

In [195]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [196]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [197]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [198]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.0 out of 5 stars\n'

In [199]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [200]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UK to EU AC Power Adapter Plug Adapter - Travel Charger Power Plug Adapter - Dual Inputs - Safe Grounded - Universal Socket, Plug Kit for The Most of Europe,10A/16A 240V
3.4 out of 5 stars
3.4
4
4
SAR 26.07
26.07


In [201]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [202]:
products_df18 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df18

pro_name            pro_rate  \
0   UK to EU AC Power Adapter Plug Adapter - Trave...  3.4 out of 5 stars   
1   Powerology 4 AC 3 USB & USB-C PD 35W Multiport...  4.0 out of 5 stars   
2   Belkin BSV604ar2M 6 Way/ 6 Plug 2m Surge Prote...  4.5 out of 5 stars   
3   Safemore Extension Cord Lead Electrical Surge ...  4.4 out of 5 stars   
4   Anker Extension Lead with 2 USB Ports and 4 Wa...  5.0 out of 5 stars   
5   Universal Travel Adapter, NTONPOWER Worldwide ...                 NaN   
6   LDNIO 4 Power Socket Extension 4 USB (18w) Def...  4.6 out of 5 stars   
7   Lawazim 2-Socket Extension Strip with 5 Meters...  3.7 out of 5 stars   
8   YUNSYE Power Strips Extension Lead w 6 USB Wal...  3.6 out of 5 stars   
9   فيش كهرباء Universal AU US EU to UK AC POWER P...  2.1 out of 5 stars   
10  Extension Cord 4 Way Power Strip White Extensi...  4.6 out of 5 stars   
11  Extension Lead 2 Sockets Power Strip 1.8m Exte...  4.0 out of 5 stars   
12                    Power Strips & Surge Protectors                 NaN   
13  Vertical Power Strip 4 layers, 11 outlets with...  5.0 out of 5 stars   
14  Mark 3864 High Quality Power socket Extension 10m  2.6 out of 5 stars   
15  Vertical Power Strip 4 layers, 11 outlets with...  4.0 out of 5 stars   
16  Vertical Power Strip 3 layers, 8 outlets with ...                 NaN   
17  [2-Pack]US USA America/ Canada/ EU Europe Euro...                 NaN   
18  3 Meter Extension Cord, NTONPOWER 3250W Power ...  4.2 out of 5 stars   
19                      DAEWOO 3 WAY UNIVERSAL SOCKET  5.0 out of 5 stars   
20  wafi World Travel Power adapter, all in one In...  4.0 out of 5 stars   
21  3-Socket Extension Cord with Individual on/off...  3.9 out of 5 stars   
22  PEGANT 5 Way 5M Power Extension Cord 5 Univers...  4.9 out of 5 stars   
23  Safemore Extension Cord Lead Electrical Surge ...  5.0 out of 5 stars   
24  US/Canada/Japan to KSA/UAE/UK Plug Adaptor, US...  4.7 out of 5 stars   
25  Extention Socket with USB C, Multiplug Adaptor...                 NaN   
26  Extension Lead with USB C and USB A,4 Universa...                 NaN   
27  Anker Universal Travel Adapter with 4 USB Port...  4.4 out of 5 stars   
28  iSONIC Power Socket Strip with 5 Outlets 2860W...                 NaN   
29                            Alfa NEW ALF SOCKET 13A  5.0 out of 5 stars   
30  Alitayee Plug Extension, 2 Way Plug Adapter Uk...                 NaN   
31  Tower Extension Cord Power Socket - TESSAN 11 ...  4.2 out of 5 stars   
32                        CABLE EXTENSION REEL 50 MTR  3.2 out of 5 stars   
33                  Power Socket Extension Board Cord                 NaN   
34  PDU special conversion plug UPS C13 to univers...                 NaN   
35  5pcs 3S BMS Module 12V 10A 18650 BMS Charger M...  4.0 out of 5 stars   
36  Tower Extension Cord Power Socket - TESSAN 11 ...                 NaN   
37  LENCENT 2Pcs UK to EU Euro Europe Plug Adapter...                 NaN   
38  Electrical Socket 4 Way Power Strip 3m Extensi...  4.7 out of 5 stars   
39  Premium-Line 4-Way Extension Lead Power Strip ...                 NaN   
40  Belkin SurgePlus USB Surge Protector, 2 USB 2....  4.8 out of 5 stars   
41  Multi Plug Extension Socket Adapter with 3 USB...                 NaN   
42  Extension Power Socket,ANTI STATIC POWER SOCKE...  5.0 out of 5 stars   
43  LENCENT Extension Lead with USB C Port, 4 Way ...  4.7 out of 5 stars   
44  Terminator Soldering Past 50g - - Paste Flux f...  4.4 out of 5 stars   
45  HOOPO-Power Strip with 6 USB 3 Power Socket 5....  5.0 out of 5 stars   
46  Extension Cord Tower Vertical Surge Protector ...  4.6 out of 5 stars   
47  UK to EU Euro Europe Plug Adapter with 3 USB P...  5.0 out of 5 stars   
48  LENCENT Extension Lead with USB Slots, 4 Way O...  4.5 out of 5 stars   
49  SAA Approved KSA/UAE/UK/US/JP/CA to AU/NZ Adap...  3.1 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             3.4          4             

# Best Sellers in Computer Tablets (Page 1)

In [203]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966433031/ref=zg_bs_nav_1_electronics"

In [204]:
response = requests.get(url)
response.status_code

200

In [205]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [206]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [207]:

print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [208]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.4 out of 5 stars\n'

In [209]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [210]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB RAM, LTE, Gray (KSA Version)
3.2 out of 5 stars
3.2
10
10
SAR 595.00
595.00


In [211]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [212]:
products_df19 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df19

pro_name            pro_rate  \
0   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
1   2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
2   2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
3   Samsung Electronics A7 Tablet 10.4 Wi-Fi 64GB ...  4.1 out of 5 stars   
4   2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.9 out of 5 stars   
5   Samsung Electronics Galaxy Tab S7 Wi-Fi, Mysti...  4.7 out of 5 stars   
6   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
7   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
8   HUION HS64 Graphics Drawing Tablet with Batter...  4.4 out of 5 stars   
9   Microsoft Surface GO 2 [STV-00005], Tablet-PC,...  4.5 out of 5 stars   
10  Samsung Galaxy Tab S7+ Wi-Fi, Mystic Black - 2...  4.7 out of 5 stars   
11  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
12  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
13  2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Spac...  4.2 out of 5 stars   
14  2021 Apple iPad Pro (11-inch, Wi-Fi, 256GB) - ...  4.6 out of 5 stars   
15  Samsung Electronics Tab A7 Lite 8.7" Silver 32...  3.5 out of 5 stars   
16  Lenovo Smart Tab M10 Plus, 10.3" Android Table...  4.2 out of 5 stars   
17  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.6 out of 5 stars   
18  Samsung Electronics Galaxy Tab S7 FE 2021 Andr...  4.4 out of 5 stars   
19  Samsung Galaxy Tab S7 Wi-Fi, Mystic Navy - 256 GB  4.7 out of 5 stars   
20  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
21  Pritom 7 inch Kids Tablet, Quad Core Android 1...  3.6 out of 5 stars   
22  5G WiFi 2 in 1 Tablet 10 inch Android 10.0 Tab...  3.0 out of 5 stars   
23     2021 Apple iPad mini (Wi-Fi, 64GB) - Starlight  4.1 out of 5 stars   
24  Lenovo Tab P11 (TB-J606L) 11 inch Tablet, Wi-F...  5.0 out of 5 stars   
25  C idea CM810 Android Tablet, 8 Inch Tablets wi...                 NaN   
26  C idea CM810 Android Tablet, 8 Inch Tablets wi...                 NaN   
27  Other 2724602275984 in 1 Precision Screwdriver...  4.2 out of 5 stars   
28  Huawei Matepad T10S, 10.1", WIFI, 32GB, Deepse...  3.1 out of 5 stars   
29  Lenovo M7 (TB-7305X) 7 Inch Tablet, Wi-Fi + Ce...  3.7 out of 5 stars   
30  2021 Apple 10.2-inch iPad (Wi-Fi, 256GB) - Spa...  4.2 out of 5 stars   
31  Slim Folio Pro for iPad Pro 11-inch (1st and 2...  4.0 out of 5 stars   
32  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.5 out of 5 stars   
33  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
34  ATOUCH K96 7 inch Kids Tablet, 32GB ROM,3GB RA...                 NaN   
35  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  3.4 out of 5 stars   
36  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
37  2021 Apple iPad Pro (11-inch, Wi-Fi, 512GB) - ...  4.6 out of 5 stars   
38  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.5 out of 5 stars   
39    2021 Apple iPad mini (Wi-Fi, 64GB) - Space Grey  4.1 out of 5 stars   
40  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
41          2021 Apple iPad mini (Wi-Fi, 64GB) - Pink  4.1 out of 5 stars   
42  SAMSUNG Galaxy Tab S6 Lite 10.4-inch Android T...  3.9 out of 5 stars   
43  2020 Apple iPad Air (10.9-inch, Wi-Fi, 256GB) ...  4.4 out of 5 stars   
44  HUAWEI MatePad Tablet,10.4-inch FullView displ...  3.9 out of 5 stars   
45  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
46  Microsoft Surface Pro X 2-in-1 Laptop - Detach...                 NaN   
47  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.9 out of 5 stars   
48  Lenovo Tab M7 GEN 3 (2GB+32GB)*[ORIGINAL] LENO...                 NaN   
49  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.2         10           

# Best Sellers in Computer Tablets (Page 2)

In [213]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966433031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [214]:
response = requests.get(url)
response.status_code

200

In [215]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [216]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [217]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [218]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n2.8 out of 5 stars\n'

In [219]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [220]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

2021 Apple iPad Pro (12.9-inch, Wi-Fi + Cellular, 256GB) - Space Grey (5th Generation)
4.9 out of 5 stars
4.9
27
27
SAR 6,199.00
6199.00


In [221]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [222]:
products_df20 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df20

pro_name            pro_rate  \
0   2021 Apple iPad Pro (12.9-inch, Wi-Fi + Cellul...  4.9 out of 5 stars   
1   Kids tablets Datazone, 7.0 inch Dual Camera Wi...  2.8 out of 5 stars   
2   Microsoft Surface Go 2 Tablet STQ-00005, Intel...  4.2 out of 5 stars   
3   Atouch Tablet, Kids Tab A10,10.1 inch Tablet,D...                 NaN   
4   Samsung Galaxy Tab S7 FE 2021 Android Tablet 1...  4.5 out of 5 stars   
5   Samsung Galaxy Tab S7+ Wi-Fi, Mystic Black - 5...  4.7 out of 5 stars   
6    2021 Apple iPad mini (Wi-Fi, 256GB) - Space Grey  4.1 out of 5 stars   
7   Hyjoy 8 inch Kids Tablet, 1920 1200 IPS FHD Di...  4.3 out of 5 stars   
8   Lenovo Tab P11 with Keyboard Pack and Precisio...  4.0 out of 5 stars   
9   SAMSUNG Galaxy Tab S6, 10.5", 6G RAM, 128GB, L...  4.7 out of 5 stars   
10  4K Screen Tablet 10.1 inch System 8.0 Tablet P...  5.0 out of 5 stars   
11  Xiaomi Pad 5 11" Tablet, 128GB, 6GB RAM, Wi-Fi...                 NaN   
12  SAMSUNG Galaxy Tab S7+ Plus 12.4-inch Android ...  4.7 out of 5 stars   
13  2020 Apple iPad Air (10.9-inch, Wi-Fi, 256GB) ...  4.4 out of 5 stars   
14  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 256GB) ...  4.9 out of 5 stars   
15  Samsung Galaxy Tab S7 Wi-Fi, Mystic Black - 512GB  4.7 out of 5 stars   
16  Tablet 10.1 inch Android Go 11.0 Tablet PC, 6G...                 NaN   
17  Microsoft Surface Go3 64GB, 4GB RAM, Pentium G...                 NaN   
18  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 6...  4.2 out of 5 stars   
19  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 512GB) ...  4.9 out of 5 stars   
20  NEW Microsoft Surface Duo 256GB (Unlocked) - G...  4.1 out of 5 stars   
21  Samsung Galaxy Tab S6 Lite 10.4", 64GB WiFi An...  4.3 out of 5 stars   
22  Samsung Galaxy Tab S6 Lite 10.4", 64GB Wi-Fi T...  3.9 out of 5 stars   
23  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 6...  4.2 out of 5 stars   
24  AVITA Magus II 10.1" HD Tablet with Detachable...  4.0 out of 5 stars   
25  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
26  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 2...  4.2 out of 5 stars   
27  2 in 1 Android 10.0 Tablet 10 Inch 5G Dual WiF...  3.7 out of 5 stars   
28  SAMSUNG Galaxy Tab S7 Wi-Fi, Mystic Silver - 2...  4.7 out of 5 stars   
29  ALCATEL 1T7 9309X1 32GB+1GB WIFI ARABIC MINT G...  2.0 out of 5 stars   
30  Apple iPad Air 10.9" (2020-4th Gen), Wi-Fi+Cel...                 NaN   
31  HUAWEI MatePad T 10 Kids Edition, 9.7’’ Tablet...                 NaN   
32  Samsung Galaxy Tab S7 FE Tablet - 64GB, 4GB RA...  2.0 out of 5 stars   
33   2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Silver  4.2 out of 5 stars   
34  Lenovo Tab M10 (TB-X505X), 10.1 Inch Tablet, 1...  3.8 out of 5 stars   
35  Samsung Electronics Galaxy Tab S7+ Wi-Fi, Myst...  4.7 out of 5 stars   
36    2021 Apple iPad mini (Wi-Fi, 256GB) - Starlight  4.1 out of 5 stars   
37  Tablet for Toddlers Tablet Android Kids Tablet...  3.6 out of 5 stars   
38  Samsung Electronics Tab A7 Lite 8.7" Gray 32GB...  3.5 out of 5 stars   
39  Lenovo Tab M8 HD 2ND GEN (TB-8505F), 8 inch Ta...  3.8 out of 5 stars   
40  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 2...  4.2 out of 5 stars   
41  Apple iPad Pro (11-inch, Wi-Fi, 1TB) - Space Grey  5.0 out of 5 stars   
42  samsung galaxy tab s7 plus, 128 GB, 6 GB RAM, ...  4.5 out of 5 stars   
43  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
44  Lenovo Tab M7 (TB-7305X) 7 inch Tablet, Wi-Fi ...  3.2 out of 5 stars   
45  Samsung Galaxy Tab S6 Lite, 64GB, 4GB RAM, Wi-...  4.3 out of 5 stars   
46  Lenovo Smart Tab M10 Plus, FHD 10.3" Android T...  4.2 out of 5 stars   
47  IPad AIR الجيل الرابع 10.9 حالة لوحة المفاتيح ...  5.0 out of 5 stars   
48  Lenovo Tab M10 HD (2nd Gen), X306F, 10.1"HD Ta...                 NaN   
49  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.9         27           

# Best Sellers in Home Video Projectors (Page 1 )

In [223]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966457031/ref=zg_bs_nav_2_16966392031"

In [224]:
response = requests.get(url)
response.status_code

200

In [225]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [226]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [227]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [228]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'SAR 256.95'

In [229]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [230]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

YG-300 LCD Mini Portable Projector with USB/SD/AV/HDMI Slots - Yellow
2.6 out of 5 stars
2.6
160
160
SAR 153.00
153.00


In [231]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [232]:
products_df21 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df21

pro_name            pro_rate  \
0   YG-300 LCD Mini Portable Projector with USB/SD...  2.6 out of 5 stars   
1   Mini Projector - Portable Smart Home Mobile Ph...                 NaN   
2   XGIMI MoGo Pro+ portable smart home projector,...                 NaN   
3   Video Projector 3D DLP 1080P HD 3800 Lumens Wi...  3.6 out of 5 stars   
4   FunLites Upgraded Full HD Projector, Native 10...  4.1 out of 5 stars   
5   BlissLights Sky Lite - LED Laser Star Projecto...  4.6 out of 5 stars   
6             Benq Proiector DLP 3,600 lumens , White  3.9 out of 5 stars   
7   Fegishilly 3 in 1 Star Galaxy Projector Moving...                 NaN   
8   Anker Nebula Solar Portable 1080p Projector, F...                 NaN   
9   Star Projector, Galaxy Projector with Remote C...  4.5 out of 5 stars   
10  AnneFish Projector Portable Home Office HD Sup...  3.5 out of 5 stars   
11  Docooler LCD T6 Smart Wifi Projector Support 1...  2.8 out of 5 stars   
12  Festnight LCD T6 Smart Wifi Projector Support ...  2.2 out of 5 stars   
13  4600lux Portable Video Projector, Full HD 1080...  4.1 out of 5 stars   
14             LG CineBeam Portable PH510PG DLP 550Lm  4.3 out of 5 stars   
15  Annefish Wireless Portable Projector HD Suppor...                 NaN   
16  XGIMI 4K home theater projector, HDR10 movie p...                 NaN   
17  Portable Mini LED VGA, USB & HDMI Projector fo...  2.1 out of 5 stars   
18                           BenQ DLP Projector - GV1  3.6 out of 5 stars   
19  JMGO Explorer Wireless Mini Projector P2 Pro 7...  3.8 out of 5 stars   
20  Movie Projector, TOUMEI Portable Projector k1 ...  3.6 out of 5 stars   
21  UNIC T6 Mini Projector 3500 Lumins  1280X720 F...  2.9 out of 5 stars   
22  PHLIGHT Mini Projector, Home projector 800 Lum...                 NaN   
23  TOPTRO 5G WiFi Bluetooth Projector with Carryi...  4.5 out of 5 stars   
24  Nebula Apollo, Wi-Fi Mini Projector, 200 ANSI ...  3.6 out of 5 stars   
25  Decdeal Mini Portable LED Projector 4500 Lumen...  5.0 out of 5 stars   
26  UBEYS YT-500 Mini Projector Portable Outdoor P...  1.0 out of 5 stars   
27  AnneFish Mini Projector Mini Portable Smart Ho...  3.5 out of 5 stars   
28  Mini Video Projector with 6500 Brightness, 108...                 NaN   
29  Fegishilly 3 in 1 Star Galaxy Projector Moving...                 NaN   
30  Mini Projector for iPhone, 2020 WiFi Movie Pro...  5.0 out of 5 stars   
31  Wifi Bluetooth Projector Support 1080P Full HD...  4.4 out of 5 stars   
32  YUNSYE WiFi Mini Projector, Outdoor Movie Proj...  3.5 out of 5 stars   
33  Mini Projector, Portable Projector for Cartoon...  1.4 out of 5 stars   
34       Nebula Capsule Smart Mini Projector By Anker  5.0 out of 5 stars   
35  FunLites Projector,+80% Brightness HD 4900LUX ...  3.9 out of 5 stars   
36  Nebula Capsule, by Anker, Smart Wi-Fi Mini Pro...  3.8 out of 5 stars   
37  LITENERGY LED Sky Projector Light, Galaxy Ligh...  3.8 out of 5 stars   
38  Lenovo Mini Projector M1 Portable Pico Smart D...  3.9 out of 5 stars   
39  C00LBABY Star Projector Night Light, 2 in 1 St...  4.1 out of 5 stars   
40  ViewSonic M2 1080p Portable Projector with 120...  4.1 out of 5 stars   
41  YG-400 PLUS digital projector, 1200 Lumens, Fu...  3.3 out of 5 stars   
42  FunLites 4600lux Portable Video Projector,Supp...  4.1 out of 5 stars   
43  Funlites Upgraded Mini Projector, Full HD 1080...  4.1 out of 5 stars   
44  Wownect T6 WiFi Home Theater LED Projector, 35...  3.5 out of 5 stars   
45  4K WiFi Projector, Full HD 1080P Bluetooth Pro...                 NaN   
46  Mini Portable Yg400 Projector 1080p With 1200 ...  2.9 out of 5 stars   
47  Mini Projector, LED Pico Pocket Video Projecto...                 NaN   
48  Latest Upgrade 7500Lumens Mini Projector for O...                 NaN   
49  Aodin M6 D02 Mini Mobile Smart Projector 1080p...  3.5 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             2.6        160           

# Best Sellers in Home Video Projectors (Page 2 )

In [233]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966457031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [234]:
response = requests.get(url)
response.status_code

200

In [235]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [236]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [237]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [238]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.5 out of 5 stars\n'

In [239]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [240]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

ViewSonic M1 Mini DLP Pico Projector, 50 Lumens
4.0 out of 5 stars
4.0
3,030
3030
SAR 829.00
829.00


In [242]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [243]:
products_df22 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df22

pro_name            pro_rate  \
0     ViewSonic M1 Mini DLP Pico Projector, 50 Lumens  4.0 out of 5 stars   
1                         BenQ Portable Projector GV1  3.5 out of 5 stars   
2   MO C9 Mini LED Projector Supports Full HD 1080...  3.2 out of 5 stars   
3   Mini Projector, ELIKLIV Native 1080P Projector...  1.7 out of 5 stars   
4   MOTIM YG300 LED Projector 1080P Projection Mac...                 NaN   
5   Epson EB-FH06 3LCD, Full HD, 3500 Lumens, 332 ...  4.4 out of 5 stars   
6   Aproca Hard Travel Case Compatible with Anker ...  4.9 out of 5 stars   
7   Annefish Projector Portable Wifi Wireless High...                 NaN   
8   DLP Link 3D Gl 144Hz Rechargeable 3D Active Sh...  4.3 out of 5 stars   
9               Mini Smart Android Wireless Projector  2.7 out of 5 stars   
10  Epson EF-11 3LCD, Full HD, Laser, 1,000 Lumens...  4.4 out of 5 stars   
11  KODAK Luma 150 Ultra Mini Pocket Pico Projecto...  4.2 out of 5 stars   
12  Epson EH-TW7400 3LCD, 4K Pro UHD Super Resolut...  4.8 out of 5 stars   
13  J&H Professional Full HD 1080P [Bluetooth] Sup...                 NaN   
14  Hd 1080p Multimedia Led Mini Projector Home Ci...  1.4 out of 5 stars   
15  BYINTEK U50 PRO 700 Ansi Lumens 300"Inch Nativ...  5.0 out of 5 stars   
16    Full HD Smart Android Projector, White - 546332  3.4 out of 5 stars   
17  Video Projector Android Smart LED Projector R1...  3.9 out of 5 stars   
18  NEBULA D2323211 by Anker Mars II Pro 500 ANSI ...  3.3 out of 5 stars   
19  Galaxy Star Night Light for Kids - Fanrui Sola...                 NaN   
20  Projector, TOPTRO Projector with WiFi and Blue...  4.2 out of 5 stars   
21  Fegishilly 3 in 1 Star Galaxy Projector Moving...  5.0 out of 5 stars   
22  ViewSonic M1+ DLP Smart Pico Projector, 300 Lu...  4.0 out of 5 stars   
23  Starry Night Light Projector for Bedroom，Sky G...  4.5 out of 5 stars   
24                   Compatible For Samsung projector  3.0 out of 5 stars   
25  Epson EB-E10 3LCD, 3600 Lumens Brightness, 15,...  3.0 out of 5 stars   
26  BenQ Full HD 3D Projector , DLP , White , MS52...  4.4 out of 5 stars   
27  Home Projector, bonsaii 5500L WiFi Projector f...  3.6 out of 5 stars   
28                   Compatible For Samsung projector  3.4 out of 5 stars   
29  Mini Projector 2600 Lumens 2019 Upgraded Porta...                 NaN   
30  Portable Mini LED Projector Home Cinema Theate...  3.2 out of 5 stars   
31  Anker Nebula Apollo, Wi-Fi Mini Projector, 200...  4.1 out of 5 stars   
32  Lixinju Laser Star Projector,star light projec...  4.5 out of 5 stars   
33  Becailyer Galaxy Star Projector Night Light wi...                 NaN   
34  ViewSonic M1+_G2 Portable Smart Wi-Fi LED Port...                 NaN   
35                             LED Projector - YG-510  2.3 out of 5 stars   
36  NXENTC Star Projector, Star Projector Light wi...  4.4 out of 5 stars   
37  Viewsonic M1 Mini Plus Pocket Led Ultra Portab...  3.8 out of 5 stars   
38  ViewSonic PA503X XGA Business Projector, 3.600...  4.4 out of 5 stars   
39    Optoma LG LED Projector with HD Imaging, PH150G  3.3 out of 5 stars   
40  Epson EH-LS500W ATV 3LCD, 4K PRO-UHD, Laser, U...  4.2 out of 5 stars   
41  BenQ TH685i 1080p Gaming Projector - 4K HDR Su...  5.0 out of 5 stars   
42  BenQ EX600 XGA Smart Portable Projector, DLP, ...  3.6 out of 5 stars   
43  1080P HD Projector, WiFi Projector Bluetooth P...  4.2 out of 5 stars   
44                   Compatible For Samsung projector  5.0 out of 5 stars   
45  ViewSonic Ultra-Portable LED Projector WVGA 25...                 NaN   
46  KADISTAR D05E mini media projector wallpaper p...                 NaN   
47  PHLIGHT Mini Projector, Home projector 800 Lum...                 NaN   
48  Mini YG300 LCD Projector 400 - 600 Lumens 320 ...  3.6 out of 5 stars   
49  KODAK Luma 350 Portable Smart Projector w/Luma...  4.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean      pro_price pro_price_clean  
0             4.0      3,030          

# Best Sellers in Car Electronics (Page 1)

In [253]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966414031/ref=zg_bs_nav_2_16966386031"

In [254]:
response = requests.get(url)
response.status_code

200

In [255]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [256]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [257]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [258]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.1 out of 5 stars\n'

In [259]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""

In [260]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

70mai A500S Pro Plus+, 2K Front and Interior, Dual Camera 1944p, 1080p, Built-in GPS ADAS, WiFi Smart System, Voice Control




SAR 449.00
449.00


In [261]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [263]:
products_df23 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df23

pro_name            pro_rate  \
0   70mai A500S Pro Plus+, 2K Front and Interior, ...                 NaN   
1   Bluetooth V2.0 7 Inch 2 DIN Car Video Stereo P...  3.1 out of 5 stars   
2   Pioneer 1300W Bass Reflex Car Subwoofer With T...  4.4 out of 5 stars   
3   MMOBIEL Speaker Set Left and Right Replacement...  4.1 out of 5 stars   
4   YORKING Keyless Entry Remote Key Fob Car Repla...  4.3 out of 5 stars   
5   Horande Keyless Entry Replacement Key Fob Cove...  4.4 out of 5 stars   
6   Freewalk Disc Brake Lock, Anti-theft Motorcycl...  5.0 out of 5 stars   
7   Vgate vLinker BM Plus Bluetooth BLE OBD2 Scann...                 NaN   
8   4 Types 12V Add-a-Circuit Adapter & Fuse Kit -...  5.0 out of 5 stars   
9   Car Key Fob Keyless Entry Remote with Ignition...  4.3 out of 5 stars   
10  Toby's 170 degree CMOS Car Rear View Reverse B...  2.9 out of 5 stars   
11  Soundstream ST4.10000D Compact 4-Channel Car A...  4.1 out of 5 stars   
12  Metra 72-7800 Speaker Connector Harnesses for ...                 NaN   
13  JBL GX628 GX Series 6.5" 180W Peak Power 2-Way...  4.5 out of 5 stars   
14  Autobase Silicone Key Fob Cover for Honda Acco...  4.7 out of 5 stars   
15  Car HUD Display, OBDⅡ+ Smart Gauge High Defini...  5.0 out of 5 stars   
16  Replacement 4 Buttons Uncut Keyless Remote Key...  3.9 out of 5 stars   
17  ACDelco GM Original Equipment 214-1680 Vapor C...  4.7 out of 5 stars   
18  Music_90s RF Device Detector Hidden Camera Fin...                 NaN   
19  Ford Dedicated Cover Key Fob Case Suit For Key...                 NaN   
20  BoYaXiao 300 واط مجموعة الألواح الشمسية كاملة ...                 NaN   
21  Bluetooth Home Audio Amplifier System - Upgrad...  4.4 out of 5 stars   
22  Wireless CarPlay Adapter for Car Screen with A...  2.8 out of 5 stars   
23  اكس ام مشغل DVD شاشة لسقف السيارة مقاس 8.5 بوص...                 NaN   
24  Silicone Key Fob Cover Case fit for Ford Edge ...  4.7 out of 5 stars   
25  Bingcute Disc Brake Lock Anti-theft Motorcycle...  1.0 out of 5 stars   
26  Wsdcam 113dB Bike Alarm Wireless Vibration Mot...  4.5 out of 5 stars   
27  Decdeal Car Megaphone 5 Tone Alarm Horn 12V 11...                 NaN   
28  2-Way In-Wall In-Ceiling Speaker System - Dual...  4.5 out of 5 stars   
29  Replacement Smart Remote Key Fob 5 Button for ...  3.9 out of 5 stars   
30  Bug Detector Hidden Camera Detector - Anti Lis...  3.3 out of 5 stars   
31  2 Replacement Keyless Entry Remote Control Key...                 NaN   
32         Android Auto USB Dongle for Apple Car Play  2.3 out of 5 stars   
33  Cute Dinosaur Car Key Fob Cover Case for Honda...  4.5 out of 5 stars   
34  AEDIKO FM Dipole Antenna 300 Ohm T Shape FM An...                 NaN   
35  GoolRC Universal Car Door Lock Keyless Entry S...                 NaN   
36  Coolbestda 2Pcs Rubber 4buttons Smart Key Fob ...  4.8 out of 5 stars   
37  LemSa 2Pcs 5 Buttons Soft Silicone Smart Remot...  5.0 out of 5 stars   
38  Festnight AK370 Mini Audio Power Amplifier Por...                 NaN   
39  SaverRemotes Key Fob Compatible with Jeep Gran...  4.0 out of 5 stars   
40  Taramps TL-500 2x50 Watts-RMS Mini Compact Car...  4.2 out of 5 stars   
41  Wired Car Play Dongle - Car Multimedia Player ...  1.0 out of 5 stars   
42  SOOBA 9210S Car Entertainment Multimedia Syste...                 NaN   
43  Skar Audio VX4-ST 4-Inch 600 Watt High Compres...  4.6 out of 5 stars   
44  BNEW Android and Ios Carplay car auto Module U...  2.4 out of 5 stars   
45  70mai Hardwire Cable Kit for 24H Parking Monit...                 NaN   
46  Speaker Parking Aid Reversing Fit for Nissan T...                 NaN   
47  RV Backup Camera Wireless with 7‘’ Touch Key D...                 NaN   
48   SVS SoundPath Subwoofer Isolation System, 4-Pack  4.8 out of 5 stars   
49  Carlinkit 2021 U2W Wireless CarPlay Type C Don...  3.7 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             NaN        NaN             

In [264]:
df = pd.concat([products_df1,products_df2, products_df3, products_df4, products_df5, products_df6, products_df7, products_df8, 
             products_df9, products_df10, products_df11, products_df12, products_df13, products_df14, products_df15, 
             products_df16, products_df17, products_df18, products_df19, products_df20,products_df21,products_df22,products_df23])

In [265]:
df

pro_name            pro_rate  \
0     ViewSonic M1 Mini DLP Pico Projector, 50 Lumens  4.0 out of 5 stars   
1                         BenQ Portable Projector GV1  3.5 out of 5 stars   
2   MO C9 Mini LED Projector Supports Full HD 1080...  3.2 out of 5 stars   
3   Mini Projector, ELIKLIV Native 1080P Projector...  1.7 out of 5 stars   
4   MOTIM YG300 LED Projector 1080P Projection Mac...                 NaN   
..                                                ...                 ...   
45  70mai Hardwire Cable Kit for 24H Parking Monit...                 NaN   
46  Speaker Parking Aid Reversing Fit for Nissan T...                 NaN   
47  RV Backup Camera Wireless with 7‘’ Touch Key D...                 NaN   
48   SVS SoundPath Subwoofer Isolation System, 4-Pack  4.8 out of 5 stars   
49  Carlinkit 2021 U2W Wireless CarPlay Type C Don...  3.7 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.0      3,030             3030    SAR 829.00          829.00  
1             3.5        287              287  SAR 1,328.99         1328.99  
2             3.2          6                6    SAR 599.95          599.95  
3             1.7          3                3    SAR 479.20          479.20  
4             NaN        NaN              NaN    SAR 155.00          155.00  
..            ...        ...              ...           ...             ...  
45            NaN        NaN              NaN     SAR 97.37           97.37  
46            NaN        NaN              NaN    SAR 125.32          125.32  
47            NaN        NaN              NaN    SAR 904.39          904.39  
48            4.8      1,579             1579    SAR 225.88          225.88  
49            3.7      1,067             1067    SAR 569.43          569.43  

[1150 rows x 7 columns]

In [252]:
df['i'] = y
y=[]
for i in range (0,1000):
    y.append(i) 

NameError: name 'y' is not defined

In [250]:
df =df.set_index(df['i'])

KeyError: 'i'

In [266]:
df.isna().sum()

pro_name              0
pro_rate            128
pro_rate_clean      128
review_num          128
review_num_clean    128
pro_price            38
pro_price_clean      38
dtype: int64

In [301]:
#df.to_csv('Amazom_BestSeller_Products')
#df.to_csv(r'C:\Users\REEEM\Documents\SDAIA\project2\Linear-Regression\Amazom_BestSeller_Products', index=False)
#df.to_parquet("Amazom_BestSeller_Products.parquet")
df.to_csv(r'c:\Users\REEEM\Documents\SDAIA\project2\Linear-Regression\Amazom_BestSeller_Products.csv', sep='\t', mode='a')

In [307]:
pro_df = pd.read_csv('Amazom_BestSeller_Products')

In [308]:
pro_df.in

pro_name            pro_rate  \
0    SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1    Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                 Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3    SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.1 out of 5 stars   
4                     Apple AirPods with Charging Case  4.1 out of 5 stars   
..                                                 ...                 ...   
995  Lume Cube Broadcast Lighting Kit | Self Broadc...  4.4 out of 5 stars   
996  Slim Folio Pro for iPad Pro 11-inch (1st and 2...  4.0 out of 5 stars   
997  8" Windows Tablet with HDMI Port,1280x800 Touc...  2.5 out of 5 stars   
998  Lenovo Yoga Smart Tablet, 10.1" FHD (1920x1200...                 NaN   
999  Samsung Galaxy Tab Active3 Enterprise Edition ...  4.1 out of 5 stars   

     pro_rate_clean review_num  review_num_clean     pro_price  \
0               3.0          2               2.0    SAR 539.00   
1               1.0          2               2.0    SAR 539.00   
2               4.5        359             359.0     SAR 79.00   
3               4.1         40              40.0    SAR 499.00   
4               4.1      2,777            2777.0    SAR 475.00   
..              ...        ...               ...           ...   
995             4.4      1,044            1044.0    SAR 674.69   
996             4.0          1               1.0    SAR 505.22   
997             2.5          3               3.0    SAR 659.83   
998             NaN        NaN               NaN  SAR 1,026.26   
999             4.1         10              10.0  SAR 2,638.63   

     pro_price_clean    i  
0             539.00    0  
1             539.00    1  
2              79.00    2  
3             499.00    3  
4             475.00    4  
..               ...  ...  
995           674.69  995  
996           505.22  996  
997           659.83  997  
998          1026.26  998  
999          2638.63  999  

[1000 rows x 8 columns]

In [310]:
pro_df.isna().sum()

pro_name             0
pro_rate            77
pro_rate_clean      77
review_num          77
review_num_clean    77
pro_price           25
pro_price_clean     25
i                    0
dtype: int64